<a href="https://colab.research.google.com/github/wannasmile/colab_code_note/blob/main/BI0009.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

多分类lgb

这段代码定义了多个用于LightGBM模型的自定义损失函数类，专门处理多类别分类问题。每个类都通过重载`__call__`方法，为LightGBM提供了损失函数（grad）和Hessian矩阵（hess）的计算方式，这是LightGBM进行梯度提升计算时所需要的。下面逐一解释这些类的作用和具体实现：

### `softmax` 函数
这是一个通用的softmax函数，用于将一个向量或矩阵的每一行转化为概率分布。增加了一些数值稳定性处理，如：
- `kEps = 1e-16`：避免除零错误。
- `x = np.minimum(x, 88.7)`：限制输入的最大值，避免`exp`函数因输入过大而出错。

### `LGBACEMulti`
实现ACE（Absolute Error Criterion）的多类别版本。
- 使用softmax函数计算预测概率。
- 利用OneHotEncoder对标签进行One-Hot编码。
- 计算梯度和Hessian矩阵时，通过比较预测概率和One-Hot编码后的标签，来评估和更新模型。

### `LGBASLMulti`
实现Sigmoid的二分类逻辑回归的多类别版本，并加入了平衡正负样本的权重参数`r1`和`r2`，以及一个阈值`m`。
- 通过自定义方法`dldpXp`和`dldp2Xp2`分别计算一阶和二阶导数。
- 在计算梯度和Hessian矩阵时，根据样本是正类还是负类，应用不同的平衡参数`r1`或`r2`。

### `LGBAWEMulti`
加权误差多类别损失函数，加入了权重参数`r`和阈值`m`。
- 与`LGBACEMulti`类似，但加入了权重参数`r`来调整正负样本的损失比例。

### `LGBFLMulti`
实现Focal Loss的多类别版本，通过参数`r`来调整损失函数的聚焦能力。
- 使用自定义方法`dldpXp`和`dldp2Xp2`分别计算一阶和二阶导数，针对的是Focal Loss函数。

### `LGBWCEMulti`
加权交叉熵损失函数的多类别版本，通过参数`r`调整正负样本的损失比例。

### `LGBCBEMulti`
平衡交叉熵损失函数的多类别版本，通过参数`b`调整正负样本的平衡。
- 根据每个类中正样本的数量来调整损失函数，使得在处理不平衡数据时更加有效。

### 总结
这些自定义损失函数都是为了在多类别分类场景下优化LightGBM模型。每个函数都通过特定的方法计算softmax概率，并根据不同策略计算梯度和Hessian矩阵，以便在训练过程中优化模型参数。这些策略包括处理类别不平衡、引入阈值以避免过拟合、使用Focal Loss以更好地处理难分类的样本等。

In [ ]:
import numpy as np
from sklearn.preprocessing import OneHotEncoder


def softmax(x):
    kEps = 1e-16 # avoid 0 div
    x = np.minimum(x, 88.7) # avoid exp overflow
    e = np.exp(x)
    return e / np.expand_dims(np.sum(e, axis=1)+kEps, axis=1)


class LGBACEMulti():
    def __init__(self, m):
        self.m = m

    def __call__(self, labels, preds):
        p = softmax(preds)
        pm = np.maximum(p-self.m, 1e-7)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        grad = -encoded_label*(encoded_label-p)-(1-encoded_label)*(encoded_label-pm)
        hess = encoded_label*(encoded_label-p)*(encoded_label+p-1)+(1-encoded_label)*(encoded_label-pm)*(encoded_label+pm-1)
        return grad.reshape(grad.shape[0]*grad.shape[1], order='F'), hess.reshape(hess.shape[0]*hess.shape[1], order='F')



class LGBASLMulti():
    def __init__(self, r1, r2, m):
        self.r1 = r1
        self.r2 = r2
        self.m = m

    def __call__(self, labels, preds):
        p = softmax(preds)
        pm = np.maximum(p-self.m, 1e-7)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        pt = np.sum(p*encoded_label, axis=1, keepdims=True)

        grad = encoded_label*self.dldpXp(pt, self.r1)*(encoded_label-p)+\
            (1-encoded_label)*self.dldpXp(pt, self.r2)*(encoded_label-pm)
        hess = encoded_label*(self.dldp2Xp2(pt, self.r1)*(encoded_label-p)**2+\
            self.dldpXp(pt, self.r1)*(encoded_label-p)*(1-2*p))+\
            (1-encoded_label)*(self.dldp2Xp2(pt, self.r2)*(encoded_label-pm)**2+\
            self.dldpXp(pt, self.r2)*(encoded_label-pm)*(1-2*pm))

        return grad.reshape(grad.shape[0]*grad.shape[1], order='F'), hess.reshape(hess.shape[0]*hess.shape[1], order='F')

    def dldpXp(self, p, r): # dldp*p
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = (1-p1)**(r-1)*(r*p1*np.log(p1)+p1-1)
        return result

    def dldp2Xp2(self, p, r): # dldp2*p**2
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = -(1-p1)**(r-2)*(r*(r-1)*p1**2*np.log(p1)+\
                    2*r*p1*(p1-1)-(p1-1)**2)
        return result



class LGBAWEMulti():
    def __init__(self, r, m):
        self.r = r
        self.m = m

    def __call__(self, labels, preds):
        p = softmax(preds)
        pm = np.maximum(p-self.m, 1e-7)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        grad = -self.r*encoded_label*(encoded_label-p)-(1-encoded_label)*(encoded_label-pm)
        hess = self.r*encoded_label*(encoded_label-p)*(encoded_label+p-1)+(1-encoded_label)*(encoded_label-pm)*(encoded_label+pm-1)
        return grad.reshape(grad.shape[0]*grad.shape[1], order='F'), hess.reshape(hess.shape[0]*hess.shape[1], order='F')



class LGBFLMulti():
    def __init__(self, r):
        self.r = r

    def __call__(self, labels, preds):
        p = softmax(preds)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        pt = np.sum(p*encoded_label, axis=1, keepdims=True)

        grad = self.dldpXp(pt)*(encoded_label-p)
        hess = self.dldp2Xp2(pt)*(encoded_label-p)**2+\
            self.dldpXp(pt)*(encoded_label-p)*(1-2*p)

        return grad.reshape(grad.shape[0]*grad.shape[1], order='F'), hess.reshape(hess.shape[0]*hess.shape[1], order='F')

    def dldpXp(self, p): # dldp*p
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = (1-p1)**(self.r-1)*(self.r*p1*np.log(p1)+p1-1)
        return result

    def dldp2Xp2(self, p): # dldp2*p**2
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = -(1-p1)**(self.r-2)*(self.r*(self.r-1)*p1**2*np.log(p1)+\
                    2*self.r*p1*(p1-1)-(p1-1)**2)
        return result



class LGBWCEMulti():
    def __init__(self, r):
        self.r = r

    def __call__(self, labels, preds):
        p = softmax(preds)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        grad = -self.r*encoded_label*(encoded_label-p)-(1-encoded_label)*(encoded_label-p)
        hess = self.r*encoded_label*(encoded_label-p)*(encoded_label+p-1)+(1-encoded_label)*(encoded_label-p)*(encoded_label+p-1)
        return grad.reshape(grad.shape[0]*grad.shape[1], order='F'), hess.reshape(hess.shape[0]*hess.shape[1], order='F')



class LGBCBEMulti():
    def __init__(self, b):
        self.b = b

    def __call__(self, labels, preds):
        p = softmax(preds)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        n_pos = np.sum(labels, axis=0)
        ratio = (1-self.b)/(1-self.b**n_pos)
        grad = p-encoded_label
        hess = (encoded_label-p)*(encoded_label+p-1)

        grad *= ratio
        hess *= ratio
        return grad.reshape(grad.shape[0]*grad.shape[1], order='F'), hess.reshape(hess.shape[0]*hess.shape[1], order='F')




In [ ]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 364.4/364.4 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.5/233.5 kB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 1.1 MB/s eta 0:00:00


In [ ]:
# 定义要保存的字符串
data_string = '''@relation automobile
@attribute Normalized-losses real [65.0, 256.0]
@attribute Make {alfa-romero, audi, bmw, chevrolet, dodge, honda, isuzu, jaguar, mazda, mercedes-benz, mercury, mitsubishi, nissan, peugot, plymouth, porsche, renault, saab, subaru, toyota, volkswagen, volvo}
@attribute Fuel-type {diesel, gas}
@attribute Aspiration {std, turbo}
@attribute Num-of-doors {four, two}
@attribute Body-style {hardtop, wagon, sedan, hatchback, convertible}
@attribute Drive-wheels {4wd, fwd, rwd}
@attribute Engine-location {front, rear}
@attribute Wheel-base real [86.6, 120.9]
@attribute Length real [141.1, 208.1]
@attribute Width real [60.3, 72.3]
@attribute Height real [47.8, 59.8]
@attribute Curb-weight real [1488.0, 4066.0]
@attribute Engine-type {dohc, dohcv, l, ohc, ohcf, ohcv, rotor}
@attribute Num-of-cylinders {eight, five, four, six, three, twelve, two}
@attribute Engine-size real [61.0, 326.0]
@attribute Fuel-system {1bbl, 2bbl, 4bbl, idi, mfi, mpfi, spdi, spfi}
@attribute Bore real [2.54, 3.94]
@attribute Stroke real [2.07, 4.17]
@attribute Compression-ratio real [7.0, 23.0]
@attribute Horsepower real [48.0, 288.0]
@attribute Peak-rpm real [4150.0, 6600.0]
@attribute City-mpg real [13.0, 49.0]
@attribute Highway-mpg real [16.0, 54.0]
@attribute Price real [5118.0, 45400.0]
@attribute Symboling {-2, -1, 0, 1, 2, 3}
@inputs Normalized-losses, Make, Fuel-type, Aspiration, Num-of-doors, Body-style, Drive-wheels, Engine-location, Wheel-base, Length, Width, Height, Curb-weight, Engine-type, Num-of-cylinders, Engine-size, Fuel-system, Bore, Stroke, Compression-ratio, Horsepower, Peak-rpm, City-mpg, Highway-mpg, Price
@outputs Symboling
@data
168.0,toyota,gas,std,two,sedan,rwd,front,94.5,168.7,64.0,52.6,2169.0,ohc,four,98.0,2bbl,3.19,3.03,9.0,70.0,4800.0,29.0,34.0,8058.0,1
87.0,toyota,gas,std,two,hatchback,fwd,front,95.7,158.7,63.6,54.5,1985.0,ohc,four,92.0,2bbl,3.05,3.03,9.0,62.0,4800.0,35.0,39.0,5348.0,1
125.0,mitsubishi,gas,std,four,sedan,fwd,front,96.3,172.4,65.4,51.6,2365.0,ohc,four,122.0,2bbl,3.35,3.46,8.5,88.0,5000.0,25.0,32.0,6989.0,1
128.0,nissan,gas,std,four,sedan,fwd,front,100.4,181.7,66.5,55.1,3095.0,ohcv,six,181.0,mpfi,3.43,3.27,9.0,152.0,5200.0,17.0,22.0,13499.0,0
161.0,peugot,diesel,turbo,four,sedan,rwd,front,107.9,186.7,68.4,56.7,3252.0,l,four,152.0,idi,3.7,3.52,21.0,95.0,4150.0,28.0,33.0,16900.0,0
81.0,chevrolet,gas,std,four,sedan,fwd,front,94.5,158.8,63.6,52.0,1909.0,ohc,four,90.0,2bbl,3.03,3.11,9.6,70.0,5400.0,38.0,43.0,6575.0,0
192.0,bmw,gas,std,four,sedan,rwd,front,101.2,176.8,64.8,54.3,2395.0,ohc,four,108.0,mpfi,3.5,2.8,8.8,101.0,5800.0,23.0,29.0,16925.0,0
168.0,nissan,gas,std,two,hardtop,fwd,front,95.1,162.4,63.8,53.3,2008.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,8249.0,2
94.0,volkswagen,gas,std,four,sedan,fwd,front,97.3,171.7,65.5,55.7,2275.0,ohc,four,109.0,mpfi,3.19,3.4,9.0,85.0,5250.0,27.0,34.0,8495.0,2
161.0,mitsubishi,gas,std,two,hatchback,fwd,front,93.7,157.3,64.4,50.8,1918.0,ohc,four,92.0,2bbl,2.97,3.23,9.4,68.0,5500.0,37.0,41.0,5389.0,2
110.0,dodge,gas,std,four,wagon,fwd,front,103.3,174.6,64.6,59.8,2535.0,ohc,four,122.0,2bbl,3.34,3.46,8.5,88.0,5000.0,24.0,30.0,8921.0,-1
65.0,toyota,gas,std,four,hatchback,fwd,front,102.4,175.6,66.5,53.9,2458.0,ohc,four,122.0,mpfi,3.31,3.54,8.7,92.0,4200.0,27.0,32.0,11248.0,-1
161.0,peugot,gas,turbo,four,sedan,rwd,front,108.0,186.7,68.3,56.0,3130.0,l,four,134.0,mpfi,3.61,3.21,7.0,142.0,5600.0,18.0,24.0,18150.0,0
125.0,mitsubishi,gas,turbo,four,sedan,fwd,front,96.3,172.4,65.4,51.6,2403.0,ohc,four,110.0,spdi,3.17,3.46,7.5,116.0,5500.0,23.0,30.0,9279.0,1
128.0,nissan,gas,std,two,sedan,fwd,front,94.5,165.3,63.8,54.5,1889.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,5499.0,1
103.0,nissan,gas,std,four,wagon,fwd,front,94.5,170.2,63.8,53.5,2037.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,7999.0,1
89.0,subaru,gas,std,four,wagon,fwd,front,97.0,173.5,65.4,53.0,2455.0,ohcf,four,108.0,mpfi,3.62,2.64,9.0,94.0,5200.0,25.0,31.0,10198.0,0
161.0,peugot,gas,std,four,sedan,rwd,front,107.9,186.7,68.4,56.7,3075.0,l,four,120.0,mpfi,3.46,3.19,8.4,97.0,5000.0,19.0,24.0,16630.0,0
145.0,jaguar,gas,std,four,sedan,rwd,front,113.0,199.6,69.6,52.8,4066.0,dohc,six,258.0,mpfi,3.63,4.17,8.1,176.0,4750.0,15.0,19.0,32250.0,0
137.0,honda,gas,std,two,hatchback,fwd,front,86.6,144.6,63.9,50.8,1713.0,ohc,four,92.0,1bbl,2.91,3.41,9.6,58.0,4800.0,49.0,54.0,6479.0,2
134.0,toyota,gas,std,two,hardtop,rwd,front,98.4,176.2,65.6,52.0,2679.0,ohc,four,146.0,mpfi,3.62,3.5,9.3,116.0,4800.0,24.0,30.0,11199.0,2
93.0,mercedes-benz,diesel,turbo,four,sedan,rwd,front,115.6,202.6,71.7,56.3,3770.0,ohc,five,183.0,idi,3.58,3.64,21.5,123.0,4350.0,22.0,25.0,31600.0,-1
90.0,toyota,gas,std,four,sedan,rwd,front,104.5,187.8,66.5,54.1,3131.0,dohc,six,171.0,mpfi,3.27,3.35,9.2,156.0,5200.0,20.0,24.0,15690.0,-1
197.0,toyota,gas,std,two,hatchback,rwd,front,102.9,183.5,67.7,52.0,2976.0,dohc,six,171.0,mpfi,3.27,3.35,9.3,161.0,5200.0,20.0,24.0,16558.0,3
118.0,dodge,gas,turbo,two,hatchback,fwd,front,93.7,157.3,63.8,50.8,2128.0,ohc,four,98.0,mpfi,3.03,3.39,7.6,102.0,5500.0,24.0,30.0,7957.0,1
168.0,toyota,gas,std,two,hatchback,rwd,front,94.5,168.7,64.0,52.6,2204.0,ohc,four,98.0,2bbl,3.19,3.03,9.0,70.0,4800.0,29.0,34.0,8238.0,1
118.0,dodge,gas,std,two,hatchback,fwd,front,93.7,157.3,63.8,50.8,1876.0,ohc,four,90.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,6377.0,1
106.0,nissan,gas,std,four,sedan,fwd,front,97.2,173.4,65.2,54.7,2302.0,ohc,four,120.0,2bbl,3.33,3.47,8.5,97.0,5200.0,27.0,34.0,9549.0,0
85.0,honda,gas,std,four,sedan,fwd,front,96.5,175.4,62.5,54.1,2372.0,ohc,four,110.0,1bbl,3.15,3.58,9.0,86.0,5800.0,27.0,33.0,10295.0,0
102.0,subaru,gas,std,four,sedan,fwd,front,97.2,172.0,65.4,52.5,2340.0,ohcf,four,108.0,mpfi,3.62,2.64,9.0,94.0,5200.0,26.0,32.0,9960.0,0
115.0,mazda,gas,std,four,hatchback,fwd,front,98.8,177.8,66.5,55.5,2425.0,ohc,four,122.0,2bbl,3.39,3.39,8.6,84.0,4800.0,26.0,32.0,11245.0,0
104.0,saab,gas,std,four,sedan,fwd,front,99.1,186.6,66.5,56.1,2695.0,ohc,four,121.0,mpfi,3.54,3.07,9.3,110.0,5250.0,21.0,28.0,12170.0,2
122.0,volkswagen,diesel,std,two,sedan,fwd,front,97.3,171.7,65.5,55.7,2261.0,ohc,four,97.0,idi,3.01,3.4,23.0,52.0,4800.0,37.0,46.0,7775.0,2
94.0,volkswagen,diesel,std,four,sedan,fwd,front,97.3,171.7,65.5,55.7,2264.0,ohc,four,97.0,idi,3.01,3.4,23.0,52.0,4800.0,37.0,46.0,7995.0,2
95.0,volvo,gas,turbo,four,sedan,rwd,front,109.1,188.8,68.8,55.5,3049.0,ohc,four,141.0,mpfi,3.78,3.15,8.7,160.0,5300.0,19.0,25.0,19045.0,-1
74.0,volvo,gas,std,four,wagon,rwd,front,104.3,188.8,67.2,57.5,3034.0,ohc,four,141.0,mpfi,3.78,3.15,9.5,114.0,5400.0,23.0,28.0,13415.0,-1
119.0,plymouth,gas,std,two,hatchback,fwd,front,93.7,157.3,63.8,50.8,1918.0,ohc,four,90.0,2bbl,2.97,3.23,9.4,68.0,5500.0,37.0,41.0,5572.0,1
154.0,plymouth,gas,std,four,sedan,fwd,front,93.7,167.3,63.8,50.8,1989.0,ohc,four,90.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,6692.0,1
188.0,bmw,gas,std,two,sedan,rwd,front,101.2,176.8,64.8,54.3,2710.0,ohc,six,164.0,mpfi,3.31,3.19,9.0,121.0,4250.0,21.0,28.0,20970.0,0
101.0,honda,gas,std,two,hatchback,fwd,front,93.7,150.0,64.0,52.6,1837.0,ohc,four,79.0,1bbl,2.91,3.07,10.1,60.0,5500.0,38.0,42.0,5399.0,1
122.0,nissan,gas,std,four,sedan,fwd,front,94.5,165.3,63.8,54.5,1971.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,7499.0,1
154.0,plymouth,gas,std,four,sedan,fwd,front,93.7,167.3,63.8,50.8,2191.0,ohc,four,98.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,7609.0,1
161.0,mitsubishi,gas,turbo,two,hatchback,fwd,front,93.0,157.3,63.8,50.8,2145.0,ohc,four,98.0,spdi,3.03,3.39,7.6,102.0,5500.0,24.0,30.0,7689.0,1
98.0,chevrolet,gas,std,two,hatchback,fwd,front,94.5,155.9,63.6,52.0,1874.0,ohc,four,90.0,2bbl,3.03,3.11,9.6,70.0,5400.0,38.0,43.0,6295.0,1
150.0,saab,gas,turbo,two,hatchback,fwd,front,99.1,186.6,66.5,56.1,2808.0,dohc,four,121.0,mpfi,3.54,3.07,9.0,160.0,5500.0,19.0,26.0,18150.0,3
161.0,peugot,gas,std,four,sedan,rwd,front,107.9,186.7,68.4,56.7,3020.0,l,four,120.0,mpfi,3.46,3.19,8.4,97.0,5000.0,19.0,24.0,11900.0,0
91.0,toyota,diesel,std,four,hatchback,fwd,front,95.7,166.3,64.4,52.8,2275.0,ohc,four,110.0,idi,3.27,3.35,22.5,56.0,4500.0,38.0,47.0,7788.0,0
91.0,toyota,gas,std,four,wagon,4wd,front,95.7,169.7,63.6,59.1,3110.0,ohc,four,92.0,2bbl,3.05,3.03,9.0,62.0,4800.0,27.0,32.0,8778.0,0
134.0,toyota,gas,std,two,hatchback,rwd,front,98.4,176.2,65.6,52.0,2714.0,ohc,four,146.0,mpfi,3.62,3.5,9.3,116.0,4800.0,24.0,30.0,11549.0,2
192.0,bmw,gas,std,two,sedan,rwd,front,101.2,176.8,64.8,54.3,2395.0,ohc,four,108.0,mpfi,3.5,2.8,8.8,101.0,5800.0,23.0,29.0,16430.0,2
104.0,saab,gas,std,four,sedan,fwd,front,99.1,186.6,66.5,56.1,2758.0,ohc,four,121.0,mpfi,3.54,3.07,9.3,110.0,5250.0,21.0,28.0,15510.0,2
95.0,volvo,gas,turbo,four,sedan,rwd,front,109.1,188.8,68.9,55.5,3062.0,ohc,four,141.0,mpfi,3.78,3.15,9.5,114.0,5400.0,19.0,25.0,22625.0,-1
65.0,toyota,gas,std,four,hatchback,fwd,front,102.4,175.6,66.5,53.9,2414.0,ohc,four,122.0,mpfi,3.31,3.54,8.7,92.0,4200.0,27.0,32.0,9988.0,-1
150.0,saab,gas,std,two,hatchback,fwd,front,99.1,186.6,66.5,56.1,2707.0,ohc,four,121.0,mpfi,2.54,2.07,9.3,110.0,5250.0,21.0,28.0,15040.0,3
87.0,toyota,gas,std,two,hatchback,fwd,front,95.7,158.7,63.6,54.5,2040.0,ohc,four,92.0,2bbl,3.05,3.03,9.0,62.0,4800.0,31.0,38.0,6338.0,1
128.0,nissan,gas,std,two,hatchback,fwd,front,94.5,165.6,63.8,53.3,2028.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,7799.0,1
104.0,mazda,gas,std,two,hatchback,fwd,front,93.1,159.1,64.2,54.1,1905.0,ohc,four,91.0,2bbl,3.03,3.15,9.0,68.0,5000.0,31.0,38.0,6795.0,1
74.0,toyota,gas,std,four,hatchback,fwd,front,95.7,158.7,63.6,54.5,2015.0,ohc,four,92.0,2bbl,3.05,3.03,9.0,62.0,4800.0,31.0,38.0,6488.0,1
119.0,plymouth,gas,turbo,two,hatchback,fwd,front,93.7,157.3,63.8,50.8,2128.0,ohc,four,98.0,spdi,3.03,3.39,7.6,102.0,5500.0,24.0,30.0,7957.0,1
153.0,mitsubishi,gas,turbo,two,hatchback,fwd,front,96.3,173.0,65.4,49.4,2370.0,ohc,four,110.0,spdi,3.17,3.46,7.5,116.0,5500.0,23.0,30.0,9959.0,3
102.0,subaru,gas,std,four,sedan,4wd,front,97.0,172.0,65.4,54.3,2385.0,ohcf,four,108.0,2bbl,3.62,2.64,9.0,82.0,4800.0,24.0,25.0,9233.0,0
78.0,honda,gas,std,four,wagon,fwd,front,96.5,157.1,63.9,58.3,2024.0,ohc,four,92.0,1bbl,2.92,3.41,9.2,76.0,6000.0,30.0,34.0,7295.0,0
85.0,honda,gas,std,four,sedan,fwd,front,96.5,175.4,65.2,54.1,2304.0,ohc,four,110.0,1bbl,3.15,3.58,9.0,86.0,5800.0,27.0,33.0,8845.0,0
108.0,nissan,gas,std,four,sedan,fwd,front,100.4,184.6,66.5,55.1,3060.0,ohcv,six,181.0,mpfi,3.43,3.27,9.0,152.0,5200.0,19.0,25.0,13499.0,0
81.0,toyota,gas,std,four,wagon,4wd,front,95.7,169.7,63.6,59.1,2290.0,ohc,four,92.0,2bbl,3.05,3.03,9.0,62.0,4800.0,27.0,32.0,7898.0,0
122.0,volkswagen,gas,std,two,sedan,fwd,front,97.3,171.7,65.5,55.7,2209.0,ohc,four,109.0,mpfi,3.19,3.4,9.0,85.0,5250.0,27.0,34.0,7975.0,2
83.0,subaru,gas,std,two,hatchback,fwd,front,93.7,157.9,63.6,53.7,2120.0,ohcf,four,108.0,2bbl,3.62,2.64,8.7,73.0,4400.0,26.0,31.0,7053.0,2
95.0,volvo,diesel,turbo,four,sedan,rwd,front,109.1,188.8,68.9,55.5,3217.0,ohc,six,145.0,idi,3.01,3.4,23.0,106.0,4800.0,26.0,27.0,22470.0,-1
91.0,toyota,gas,std,four,sedan,fwd,front,95.7,166.3,64.4,52.8,2140.0,ohc,four,98.0,2bbl,3.19,3.03,9.0,70.0,4800.0,28.0,34.0,9258.0,0
103.0,volvo,gas,std,four,sedan,rwd,front,104.3,188.8,67.2,56.2,2912.0,ohc,four,141.0,mpfi,3.78,3.15,9.5,114.0,5400.0,23.0,28.0,12940.0,-2
231.0,nissan,gas,std,two,hatchback,rwd,front,99.2,178.5,67.9,49.7,3139.0,ohcv,six,181.0,mpfi,3.43,3.27,9.0,160.0,5200.0,19.0,25.0,18399.0,1
148.0,dodge,gas,std,four,sedan,fwd,front,93.7,157.3,63.8,50.6,1989.0,ohc,four,90.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,6692.0,1
142.0,mercedes-benz,gas,std,two,convertible,rwd,front,96.6,180.3,70.5,50.8,3685.0,ohcv,eight,234.0,mpfi,3.46,3.1,8.3,155.0,4750.0,16.0,18.0,35056.0,3
91.0,toyota,gas,std,four,hatchback,fwd,front,95.7,166.3,64.4,52.8,2122.0,ohc,four,98.0,2bbl,3.19,3.03,9.0,70.0,4800.0,28.0,34.0,8358.0,0
93.0,mercedes-benz,diesel,turbo,two,hardtop,rwd,front,106.7,187.5,70.3,54.9,3495.0,ohc,five,183.0,idi,3.58,3.64,21.5,123.0,4350.0,22.0,25.0,28176.0,0
104.0,saab,gas,turbo,four,sedan,fwd,front,99.1,186.6,66.5,56.1,2847.0,dohc,four,121.0,mpfi,3.54,3.07,9.0,160.0,5500.0,19.0,26.0,18620.0,2
121.0,chevrolet,gas,std,two,hatchback,fwd,front,88.4,141.1,60.3,53.2,1488.0,l,three,61.0,2bbl,2.91,3.03,9.5,48.0,5100.0,47.0,53.0,5151.0,2
65.0,toyota,gas,std,four,sedan,fwd,front,102.4,175.6,66.5,54.9,2326.0,ohc,four,122.0,mpfi,3.31,3.54,8.7,92.0,4200.0,29.0,34.0,8948.0,-1
134.0,toyota,gas,std,two,hatchback,rwd,front,98.4,176.2,65.6,52.0,2551.0,ohc,four,146.0,mpfi,3.62,3.5,9.3,116.0,4800.0,24.0,30.0,9989.0,2
148.0,dodge,gas,std,four,sedan,fwd,front,93.7,157.3,63.8,50.6,1989.0,ohc,four,90.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,7609.0,1
118.0,dodge,gas,std,two,hatchback,fwd,front,93.7,157.3,63.8,50.8,1876.0,ohc,four,90.0,2bbl,2.97,3.23,9.41,68.0,5500.0,37.0,41.0,5572.0,1
85.0,subaru,gas,turbo,four,wagon,4wd,front,96.9,173.6,65.4,54.9,2650.0,ohcf,four,108.0,mpfi,3.62,2.64,7.7,111.0,4800.0,23.0,23.0,11694.0,0
91.0,toyota,diesel,std,four,sedan,fwd,front,95.7,166.3,64.4,53.0,2275.0,ohc,four,110.0,idi,3.27,3.35,22.5,56.0,4500.0,34.0,36.0,7898.0,0
110.0,honda,gas,std,four,sedan,fwd,front,96.5,163.4,64.0,54.5,2010.0,ohc,four,92.0,1bbl,2.91,3.41,9.2,76.0,6000.0,30.0,34.0,7295.0,0
108.0,nissan,gas,std,four,wagon,fwd,front,100.4,184.6,66.5,56.1,3296.0,ohcv,six,181.0,mpfi,3.43,3.27,9.0,152.0,5200.0,17.0,22.0,14399.0,0
102.0,subaru,gas,turbo,four,sedan,4wd,front,97.0,172.0,65.4,54.3,2510.0,ohcf,four,108.0,mpfi,3.62,2.64,7.7,111.0,4800.0,24.0,29.0,11259.0,0
161.0,mitsubishi,gas,std,two,hatchback,fwd,front,93.7,157.3,64.4,50.8,1944.0,ohc,four,92.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,6189.0,2
107.0,honda,gas,std,two,sedan,fwd,front,96.5,169.1,66.0,51.0,2293.0,ohc,four,110.0,2bbl,3.15,3.58,9.1,100.0,5500.0,25.0,31.0,10345.0,1
113.0,mazda,gas,std,four,sedan,fwd,front,93.1,166.8,64.2,54.1,1945.0,ohc,four,91.0,2bbl,3.03,3.15,9.0,68.0,5000.0,31.0,38.0,6695.0,1
158.0,audi,gas,turbo,four,sedan,fwd,front,105.8,192.7,71.4,55.9,3086.0,ohc,five,131.0,mpfi,3.13,3.4,8.3,140.0,5500.0,17.0,20.0,23875.0,1
125.0,mitsubishi,gas,std,four,sedan,fwd,front,96.3,172.4,65.4,51.6,2405.0,ohc,four,122.0,2bbl,3.35,3.46,8.5,88.0,5000.0,25.0,32.0,8189.0,1
145.0,dodge,gas,turbo,two,hatchback,fwd,front,95.9,173.2,66.3,50.2,2811.0,ohc,four,156.0,mfi,3.6,3.9,7.0,145.0,5000.0,19.0,24.0,12964.0,3
91.0,toyota,gas,std,four,sedan,fwd,front,95.7,166.3,64.4,53.0,2081.0,ohc,four,98.0,2bbl,3.19,3.03,9.0,70.0,4800.0,30.0,37.0,6938.0,0
115.0,mazda,gas,std,four,sedan,fwd,front,98.8,177.8,66.5,55.5,2410.0,ohc,four,122.0,2bbl,3.39,3.39,8.6,84.0,4800.0,26.0,32.0,10245.0,0
102.0,subaru,gas,std,four,sedan,fwd,front,97.2,172.0,65.4,52.5,2145.0,ohcf,four,108.0,2bbl,3.62,2.64,9.5,82.0,4800.0,32.0,37.0,7126.0,0
91.0,toyota,gas,std,four,sedan,fwd,front,95.7,166.3,64.4,53.0,2094.0,ohc,four,98.0,2bbl,3.19,3.03,9.0,70.0,4800.0,38.0,47.0,7738.0,0
134.0,toyota,gas,std,two,convertible,rwd,front,98.4,176.2,65.6,53.0,2975.0,ohc,four,146.0,mpfi,3.62,3.5,9.3,116.0,4800.0,24.0,30.0,17669.0,2
94.0,volkswagen,diesel,turbo,four,sedan,fwd,front,97.3,171.7,65.5,55.7,2319.0,ohc,four,97.0,idi,3.01,3.4,23.0,68.0,4500.0,37.0,42.0,9495.0,2
83.0,subaru,gas,std,two,hatchback,fwd,front,93.7,156.9,63.4,53.7,2050.0,ohcf,four,97.0,2bbl,3.62,2.36,9.0,69.0,4900.0,31.0,36.0,5118.0,2
65.0,toyota,diesel,turbo,four,sedan,fwd,front,102.4,175.6,66.5,54.9,2480.0,ohc,four,110.0,idi,3.27,3.35,22.5,73.0,4500.0,30.0,33.0,10698.0,-1
95.0,volvo,gas,std,four,sedan,rwd,front,109.1,188.8,68.9,55.5,3012.0,ohcv,six,173.0,mpfi,3.58,2.87,8.8,134.0,5500.0,18.0,23.0,21485.0,-1
103.0,volvo,gas,turbo,four,sedan,rwd,front,104.3,188.8,67.2,56.2,3045.0,ohc,four,130.0,mpfi,3.62,3.15,7.5,162.0,5100.0,17.0,22.0,18420.0,-2
129.0,mazda,gas,std,two,hatchback,fwd,front,98.8,177.8,66.5,53.7,2385.0,ohc,four,122.0,2bbl,3.39,3.39,8.6,84.0,4800.0,26.0,32.0,10595.0,1
128.0,nissan,diesel,std,two,sedan,fwd,front,94.5,165.3,63.8,54.5,2017.0,ohc,four,103.0,idi,2.99,3.47,21.9,55.0,4800.0,45.0,50.0,7099.0,1
91.0,toyota,gas,std,four,hatchback,fwd,front,95.7,166.3,64.4,52.8,2109.0,ohc,four,98.0,2bbl,3.19,3.03,9.0,70.0,4800.0,30.0,37.0,7198.0,0
85.0,subaru,gas,std,four,wagon,4wd,front,96.9,173.6,65.4,54.9,2420.0,ohcf,four,108.0,2bbl,3.62,2.64,9.0,82.0,4800.0,23.0,29.0,8013.0,0
134.0,toyota,gas,std,two,hardtop,rwd,front,98.4,176.2,65.6,52.0,2540.0,ohc,four,146.0,mpfi,3.62,3.5,9.3,116.0,4800.0,24.0,30.0,8449.0,2
94.0,volkswagen,gas,std,four,sedan,fwd,front,97.3,171.7,65.5,55.7,2212.0,ohc,four,109.0,mpfi,3.19,3.4,9.0,85.0,5250.0,27.0,34.0,8195.0,2
74.0,volvo,gas,std,four,wagon,rwd,front,104.3,188.8,67.2,57.5,3042.0,ohc,four,141.0,mpfi,3.78,3.15,9.5,114.0,5400.0,24.0,28.0,16515.0,-1
74.0,volvo,gas,turbo,four,wagon,rwd,front,104.3,188.8,67.2,57.5,3157.0,ohc,four,130.0,mpfi,3.62,3.15,7.5,162.0,5100.0,17.0,22.0,18950.0,-1
150.0,saab,gas,std,two,hatchback,fwd,front,99.1,186.6,66.5,56.1,2658.0,ohc,four,121.0,mpfi,3.54,3.07,9.31,110.0,5250.0,21.0,28.0,11850.0,3
194.0,nissan,gas,std,two,hatchback,rwd,front,91.3,170.7,67.9,49.7,3071.0,ohcv,six,181.0,mpfi,3.43,3.27,9.0,160.0,5200.0,19.0,25.0,17199.0,3
148.0,dodge,gas,std,four,hatchback,fwd,front,93.7,157.3,63.8,50.6,1967.0,ohc,four,90.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,6229.0,1
103.0,nissan,gas,std,four,wagon,fwd,front,94.5,170.2,63.8,53.5,2024.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,7349.0,1
101.0,honda,gas,std,two,hatchback,fwd,front,93.7,150.0,64.0,52.6,1940.0,ohc,four,92.0,1bbl,2.91,3.41,9.2,76.0,6000.0,30.0,34.0,6529.0,1
168.0,toyota,gas,std,two,hatchback,rwd,front,94.5,168.7,64.0,52.6,2300.0,dohc,four,98.0,mpfi,3.24,3.08,9.4,112.0,6600.0,26.0,29.0,9538.0,1
158.0,audi,gas,std,four,sedan,fwd,front,105.8,192.7,71.4,55.7,2844.0,ohc,five,136.0,mpfi,3.19,3.4,8.5,110.0,5500.0,19.0,25.0,17710.0,1
153.0,mitsubishi,gas,std,two,hatchback,fwd,front,96.3,173.0,65.4,49.4,2328.0,ohc,four,122.0,2bbl,3.35,3.46,8.5,88.0,5000.0,25.0,32.0,8499.0,3
161.0,peugot,gas,std,four,sedan,rwd,front,107.9,186.7,68.4,56.7,3075.0,l,four,120.0,mpfi,3.46,2.19,8.4,95.0,5000.0,19.0,24.0,15580.0,0
89.0,subaru,gas,std,four,wagon,fwd,front,97.0,173.5,65.4,53.0,2290.0,ohcf,four,108.0,2bbl,3.62,2.64,9.0,82.0,4800.0,28.0,32.0,7463.0,0
161.0,peugot,diesel,turbo,four,sedan,rwd,front,107.9,186.7,68.4,56.7,3252.0,l,four,152.0,idi,3.7,3.52,21.0,95.0,4150.0,28.0,33.0,17950.0,0
85.0,honda,gas,std,four,sedan,fwd,front,96.5,175.4,65.2,54.1,2465.0,ohc,four,110.0,mpfi,3.15,3.58,9.0,101.0,5800.0,24.0,28.0,12945.0,0
94.0,volkswagen,gas,std,four,sedan,fwd,front,97.3,171.7,65.5,55.7,2300.0,ohc,four,109.0,mpfi,3.19,3.4,10.0,100.0,5500.0,26.0,32.0,9995.0,2
65.0,toyota,gas,std,four,sedan,fwd,front,102.4,175.6,66.5,54.9,2414.0,ohc,four,122.0,mpfi,3.31,3.54,8.7,92.0,4200.0,27.0,32.0,10898.0,-1
128.0,nissan,gas,std,two,sedan,fwd,front,94.5,165.3,63.8,54.5,1918.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,6649.0,1
186.0,porsche,gas,std,two,hatchback,rwd,front,94.5,168.9,68.3,50.2,2778.0,ohc,four,151.0,mpfi,3.94,3.11,9.5,143.0,5500.0,19.0,27.0,22018.0,3
93.0,mercedes-benz,diesel,turbo,four,sedan,rwd,front,110.0,190.9,70.3,56.5,3515.0,ohc,five,183.0,idi,3.58,3.64,21.5,123.0,4350.0,22.0,25.0,25552.0,-1
113.0,mazda,gas,std,four,sedan,fwd,front,93.1,166.8,64.2,54.1,1950.0,ohc,four,91.0,2bbl,3.08,3.15,9.0,68.0,5000.0,31.0,38.0,7395.0,1
194.0,nissan,gas,turbo,two,hatchback,rwd,front,91.3,170.7,67.9,49.7,3139.0,ohcv,six,181.0,mpfi,3.43,3.27,7.8,200.0,5200.0,17.0,23.0,19699.0,3
115.0,mazda,gas,std,four,sedan,fwd,front,98.8,177.8,66.5,55.5,2410.0,ohc,four,122.0,2bbl,3.39,3.39,8.6,84.0,4800.0,26.0,32.0,8495.0,0
164.0,audi,gas,std,four,sedan,fwd,front,99.8,176.6,66.2,54.3,2337.0,ohc,four,109.0,mpfi,3.19,3.4,10.0,102.0,5500.0,24.0,30.0,13950.0,2
197.0,toyota,gas,std,two,hatchback,rwd,front,102.9,183.5,67.7,52.0,3016.0,dohc,six,171.0,mpfi,3.27,3.35,9.3,161.0,5200.0,19.0,24.0,15998.0,3
106.0,honda,gas,std,two,hatchback,fwd,front,96.5,167.5,65.2,53.3,2236.0,ohc,four,110.0,1bbl,3.15,3.58,9.0,86.0,5800.0,27.0,33.0,7895.0,0
118.0,mazda,gas,std,four,sedan,rwd,front,104.9,175.0,66.1,54.4,2670.0,ohc,four,140.0,mpfi,3.76,3.16,8.0,120.0,5000.0,19.0,27.0,18280.0,0
77.0,toyota,gas,std,four,wagon,fwd,front,95.7,169.7,63.6,59.1,2280.0,ohc,four,92.0,2bbl,3.05,3.03,9.0,62.0,4800.0,31.0,37.0,6918.0,0
122.0,nissan,gas,std,four,sedan,fwd,front,94.5,165.3,63.8,54.5,1938.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,6849.0,1
95.0,volvo,gas,std,four,sedan,rwd,front,109.1,188.8,68.9,55.5,2952.0,ohc,four,141.0,mpfi,3.78,3.15,9.5,114.0,5400.0,23.0,28.0,16845.0,-1
137.0,honda,gas,std,two,hatchback,fwd,front,86.6,144.6,63.9,50.8,1819.0,ohc,four,92.0,1bbl,2.91,3.41,9.2,76.0,6000.0,31.0,38.0,6855.0,2
74.0,plymouth,gas,std,four,wagon,fwd,front,103.3,174.6,64.6,59.8,2535.0,ohc,four,122.0,2bbl,3.35,3.46,8.5,88.0,5000.0,24.0,30.0,8921.0,-1
154.0,plymouth,gas,std,four,hatchback,fwd,front,93.7,157.3,63.8,50.6,1967.0,ohc,four,90.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,6229.0,1
129.0,mazda,gas,std,two,hatchback,fwd,front,98.8,177.8,66.5,53.7,2385.0,ohc,four,122.0,2bbl,3.39,3.39,8.6,84.0,4800.0,26.0,32.0,8845.0,1
106.0,nissan,gas,std,four,hatchback,fwd,front,97.2,173.4,65.2,54.7,2324.0,ohc,four,120.0,2bbl,3.33,3.47,8.5,97.0,5200.0,27.0,34.0,8949.0,0
256.0,volkswagen,gas,std,two,hatchback,fwd,front,94.5,165.7,64.0,51.4,2221.0,ohc,four,109.0,mpfi,3.19,3.4,8.5,90.0,5500.0,24.0,29.0,9980.0,3
103.0,volvo,gas,std,four,sedan,rwd,front,104.3,188.8,67.2,56.2,2935.0,ohc,four,141.0,mpfi,3.78,3.15,9.5,114.0,5400.0,24.0,28.0,15985.0,-2
168.0,toyota,gas,std,two,sedan,rwd,front,94.5,168.7,64.0,52.6,2265.0,dohc,four,98.0,mpfi,3.24,3.08,9.4,112.0,6600.0,26.0,29.0,9298.0,1
104.0,mazda,gas,std,two,hatchback,fwd,front,93.1,159.1,64.2,54.1,1890.0,ohc,four,91.0,2bbl,3.03,3.15,9.0,68.0,5000.0,30.0,31.0,5195.0,1
134.0,toyota,gas,std,two,hardtop,rwd,front,98.4,176.2,65.6,52.0,2536.0,ohc,four,146.0,mpfi,3.62,3.5,9.3,116.0,4800.0,24.0,30.0,9639.0,2
137.0,mitsubishi,gas,std,four,sedan,fwd,front,96.3,172.4,65.4,51.6,2403.0,ohc,four,110.0,spdi,3.17,3.46,7.5,116.0,5500.0,23.0,30.0,9279.0,-1
93.0,mercedes-benz,diesel,turbo,four,wagon,rwd,front,110.0,190.9,70.3,58.7,3750.0,ohc,five,183.0,idi,3.58,3.64,21.5,123.0,4350.0,22.0,25.0,28248.0,-1
101.0,honda,gas,std,two,hatchback,fwd,front,93.7,150.0,64.0,52.6,1956.0,ohc,four,92.0,1bbl,2.91,3.41,9.2,76.0,6000.0,30.0,34.0,7129.0,1
102.0,subaru,gas,std,four,sedan,fwd,front,97.2,172.0,65.4,52.5,2190.0,ohcf,four,108.0,2bbl,3.62,2.64,9.5,82.0,4400.0,28.0,33.0,7775.0,0
128.0,nissan,gas,std,two,sedan,fwd,front,94.5,165.3,63.8,54.5,1951.0,ohc,four,97.0,2bbl,3.15,3.29,9.4,69.0,5200.0,31.0,37.0,7299.0,1
104.0,mazda,gas,std,two,hatchback,fwd,front,93.1,159.1,64.2,54.1,1900.0,ohc,four,91.0,2bbl,3.03,3.15,9.0,68.0,5000.0,31.0,38.0,6095.0,1
106.0,honda,gas,std,two,hatchback,fwd,front,96.5,167.5,65.2,53.3,2289.0,ohc,four,110.0,1bbl,3.15,3.58,9.0,86.0,5800.0,27.0,33.0,9095.0,0
161.0,peugot,diesel,turbo,four,sedan,rwd,front,107.9,186.7,68.4,56.7,3197.0,l,four,152.0,idi,3.7,3.52,21.0,95.0,4150.0,28.0,33.0,13200.0,0
83.0,subaru,gas,std,two,hatchback,4wd,front,93.3,157.3,63.8,55.7,2240.0,ohcf,four,108.0,2bbl,3.62,2.64,8.7,73.0,4400.0,26.0,31.0,7603.0,2
188.0,bmw,gas,std,four,sedan,rwd,front,101.2,176.8,64.8,54.3,2765.0,ohc,six,164.0,mpfi,3.31,3.19,9.0,121.0,4250.0,21.0,28.0,21105.0,0
161.0,mitsubishi,gas,std,two,hatchback,fwd,front,93.7,157.3,64.4,50.8,2004.0,ohc,four,92.0,2bbl,2.97,3.23,9.4,68.0,5500.0,31.0,38.0,6669.0,2
164.0,audi,gas,std,four,sedan,4wd,front,99.4,176.6,66.4,54.3,2824.0,ohc,five,136.0,mpfi,3.19,3.4,8.0,115.0,5500.0,18.0,22.0,17450.0,2'''

# 打开文件进行写入
with open('automobile-full.dat', 'w', encoding='utf-8') as file:
    file.write(data_string)

# 文件现在包含字符串数据，并以utf-8编码保存

这段代码实现了一个使用Optuna进行超参数优化，以及使用LightGBM进行多类分类任务的示例。下面分步骤解释代码的主要功能和流程：

### 1. 导入必要的库
- 代码首先导入了NumPy、LightGBM、sklearn的一些模块（如评价指标和交叉验证工具）、pandas、LabelEncoder以及Optuna库。

### 2. 定义辅助函数
- **`predict` 和 `predict_proba`**：这两个函数用于从LightGBM模型中获取预测结果和预测概率。`predict_proba`函数通过自定义的`softmax`函数来计算预测概率。
- **`softmax`**：计算softmax概率，避免数值溢出和除零错误。
- **`eval_acc`**：自定义评估函数，计算模型的准确率。

### 3. 定义LGBMulti类
这个类用于初始化LightGBM分类器，并在Optuna的每次试验中，调整不同的超参数组合，执行交叉验证来评估模型性能。
- 在`__call__`方法中，使用StratifiedKFold进行分层交叉验证，确保每个折的训练和验证集中的类别分布一致。
- 使用Optuna的试验对象(`trial`)来建议不同的超参数值，如`num_leaves`、`learning_rate`等。
- 训练LightGBM模型，并在验证集上评估准确率。

### 4. 测试模型
- **`test` 函数**：使用最优的超参数在交叉验证的每一折上训练模型，并在独立的测试集上评估模型性能，包括准确率(`accuracy_score`)和F1分数(`f1_score`)。

### 5. 加载和预处理数据
- **`load_data` 函数**：从指定的数据文件路径加载数据，处理分类特征，并使用`LabelEncoder`对输出标签进行编码。

### 6. 数据集分割
- 将加载的数据分为训练集和测试集，确保分层（按类别比例）分割以保持类别分布。

### 7. Optuna优化过程
- 设置Optuna的日志级别和警告过滤。
- 使用TPE采样器(`TPESampler`)创建Optuna研究对象(`create_study`)，并对`LGBMulti`类执行优化搜索，寻找最佳超参数组合。

### 8. 输出结果
- 打印在测试集上的准确率和F1分数的均值和标准差。

### 总结
这段代码通过Optuna库对LightGBM模型进行超参数调优，以处理一个多类分类问题。它展示了从数据预处理、模型训练、超参数搜索到模型评估的完整流程。这样的实现对于在真实场景中应用机器学习模型非常有用，可以确保模型以最佳性能运行。

In [ ]:
import numpy as np
import lightgbm as lgb
from sklearn.metrics import accuracy_score, f1_score
from sklearn.model_selection import StratifiedKFold
import optuna
from sklearn.model_selection import train_test_split
import pandas as pd
from sklearn.preprocessing import LabelEncoder
import warnings


def predict(model, X):
    prediction_probabilities = predict_proba(model, X)
    predictions = np.argmax(prediction_probabilities, axis=1)
    return predictions

def predict_proba(model, X):
    # Lightgbm: Cannot compute class probabilities or labels due to the usage of customized objective function.
    prediction = model.predict(X)
    prediction_probabilities = softmax(prediction)
    return prediction_probabilities

def eval_acc(labels, preds):
    preds = preds.reshape((labels.shape[0], -1), order='F')
    p = softmax(preds)
    return 'eacc', accuracy_score(labels, np.argmax(p, axis=1)), True

#def softmax(x):
#    kEps = 1e-16 # avoid 0 div
#    x = np.minimum(x, 88.7) # avoid exp overflow
#    e = np.exp(x)
#    return e / np.expand_dims(np.sum(e, axis=1)+kEps, axis=1)
def softmax(x):
    kEps = 1e-16  # avoid 0 div
    x = np.minimum(x, 88.7)  # avoid exp overflow
    # Check if the input is 1-dimensional and reshape if necessary
    if x.ndim == 1:
        x = x.reshape(-1, 1)
    e = np.exp(x)
    return e / np.expand_dims(np.sum(e, axis=1) + kEps, axis=1)

class LGBMulti(object):
    def __init__(self, X, y):

        self.X = X
        self.y = y

    def __call__(self, trial):
        params = {
          "num_leaves": trial.suggest_int("num_leaves", 8, 32),
          "learning_rate": trial.suggest_float("learning_rate", 0.01, 1.0),
          "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 2.0),
          "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 2.0),
          "r": trial.suggest_categorical("r", [2.0, 3.0, 5.0]),
        }

        folds = StratifiedKFold(5, random_state=42, shuffle=True)
        scores = []
        for _, (train_idx, val_idx) in enumerate(folds.split(self.X, self.y)):
            X_tr, y_tr = self.X[train_idx], self.y[train_idx]
            X_val, y_val = self.X[val_idx], self.y[val_idx]

            # Check if y_tr and y_val have more than one unique class
            if len(np.unique(y_tr)) <= 1 or len(np.unique(y_val)) <= 1:
                # If not, skip this fold and continue to the next
                continue

            clf = lgb.LGBMClassifier(
                          n_estimators=1000,
                          learning_rate=params["learning_rate"],
                          reg_alpha=params["reg_alpha"],
                          reg_lambda=params["reg_lambda"],
                          num_leaves=params["num_leaves"],
                          #device= "gpu",
                          verbosity=-1,
                          objective="multiclass"
                          )

            clf.fit(
                X_tr, y_tr,
                eval_set=[(X_val, y_val)],
                eval_metric=eval_acc,
                callbacks=[lgb.early_stopping(stopping_rounds=50)],
                )

            y_val_pred = y_val_pred = predict(clf, X_val)
            scores.append(accuracy_score(y_val, y_val_pred))
        return np.mean(scores)



def test(best_params, X, y, X_test, y_test):
    folds = StratifiedKFold(5, random_state=42, shuffle=True)
    scores1 = []
    scores2 = []
    for _, (train_idx, val_idx) in enumerate(folds.split(X, y)):
        X_tr, y_tr = X[train_idx], y[train_idx]
        X_val, y_val = X[val_idx], y[val_idx]

        clf = lgb.LGBMClassifier(
                      n_estimators=1000,
                      num_leaves=best_params['num_leaves'],
                      reg_alpha=best_params['reg_alpha'],
                      reg_lambda=best_params['reg_lambda'],
                      learning_rate=best_params['learning_rate'],
                      #device= "gpu",
                      objective="multiclass"
                      )

        clf.fit(
            X_tr,
            y_tr,
            eval_set=[(X_val, y_val)],
            eval_metric=eval_acc,
            callbacks=[lgb.early_stopping(stopping_rounds=50)],
            )

        y_test_pred_prob = predict_proba(clf, X_test)
        y_test_pred = predict(clf, X_test)
        scores1.append(accuracy_score(y_test, y_test_pred))
        scores2.append(f1_score(y_test, y_test_pred, average="weighted"))
    return [scores1, scores2]


def load_data(path):
    with open(path) as f:
        metadata_lines = 0
        for line in f:
            if line.startswith('@'):
                metadata_lines += 1

                if line.startswith('@input'):
                    inputs = [l.strip() for l in line[8:].split(',')]
                elif line.startswith('@output'):
                    outputs = [l.strip() for l in line[8:].split(',')]
            else:
                break

    df = pd.read_csv(path, skiprows=metadata_lines, header=None)
    df.columns = inputs + outputs
    df = pd.concat([pd.get_dummies(df[inputs]), df[outputs]], axis=1)

    matrix = df.values
    X, y = matrix[:, :-1], matrix[:, -1]
    le = LabelEncoder()
    y = le.fit_transform(y)

    return X, y



X, y = load_data('automobile-full.dat')
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=42)


optuna.logging.set_verbosity(optuna.logging.ERROR)
#optuna.logging.set_verbosity(optuna.logging.WARNING)
warnings.filterwarnings("ignore", category=UserWarning)

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(
                direction="maximize",
                sampler=sampler,
                study_name='model_eval',
                )

study.optimize(LGBMulti(X_train, y_train), n_trials=100)
best_params = study.best_trial.params
scores = test(best_params, X_train, y_train, X_test, y_test)

print(scores)
print(f"ACC Mean: {np.mean(scores[1])}\n")
print(f"ACC Std: {np.std(scores[1])}\n")

#print(f"F1 Mean: {np.mean(scores[5])}\n")
#print(f"F1 Std: {np.std(scores[5])}\n")

print(f"F1 Mean: {np.mean(scores[1])}\n")
print(f"F1 Std: {np.std(scores[1])}\n")




/usr/local/lib/python3.10/dist-packages/dask/dataframe/__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[9]	valid_0's multi_logloss: 0.716966	valid_0's eacc: 0.791667
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[3]	valid_0's multi_logloss: 0.781032	valid_0's eacc: 0.833333
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[6]	valid_0's multi_logloss: 0.877642	valid_0's eacc: 0.708333
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[5]	valid_0's multi_logloss: 1.27291	valid_0's eacc: 0.666667
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[3]	valid_0's multi_logloss: 0.679727	valid_0's eacc: 0.869565
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[5]	valid_0's multi_logloss: 0.824899	valid_0's eacc: 0.708333
Training until validation scores don't improve 

In [ ]:
import numpy as np
import lightgbm as lgb
from sklearn.metrics import accuracy_score, f1_score
from sklearn.model_selection import StratifiedKFold
import optuna
from sklearn.model_selection import train_test_split
import pandas as pd
from sklearn.preprocessing import LabelEncoder
#from gbdtCBL.lgbmulti import LGBWCEMulti
import warnings


def predict(model, X):
    prediction_probabilities = predict_proba(model, X)
    predictions = np.argmax(prediction_probabilities, axis=1)
    return predictions

def predict_proba(model, X):
    # Lightgbm: Cannot compute class probabilities or labels due to the usage of customized objective function.
    prediction = model.predict(X)
    prediction_probabilities = softmax(prediction)
    return prediction_probabilities

def eval_acc(labels, preds):
    preds = preds.reshape((labels.shape[0], -1), order='F')
    p = softmax(preds)
    return 'eacc', accuracy_score(labels, np.argmax(p, axis=1)), True

def softmax(x):
    kEps = 1e-16 # avoid 0 div
    x = np.minimum(x, 88.7) # avoid exp overflow
    e = np.exp(x)
    return e / np.expand_dims(np.sum(e, axis=1)+kEps, axis=1)


class LGBMulti(object):
    def __init__(self, X, y):

        self.X = X
        self.y = y

    def __call__(self, trial):
        params = {
          "num_leaves": trial.suggest_int("num_leaves", 8, 32),
          "learning_rate": trial.suggest_float("learning_rate", 0.01, 1.0),
          "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 2.0),
          "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 2.0),
          "r": trial.suggest_categorical("r", [2.0, 3.0, 5.0]),
        }

        folds = StratifiedKFold(5, random_state=42, shuffle=True)
        scores = []
        for _, (train_idx, val_idx) in enumerate(folds.split(self.X, self.y)):
            X_tr, y_tr = self.X[train_idx], self.y[train_idx]
            X_val, y_val = self.X[val_idx], self.y[val_idx]

            clf = lgb.LGBMClassifier(
                          n_estimators=1000,
                          learning_rate=params["learning_rate"],
                          reg_alpha=params["reg_alpha"],
                          reg_lambda=params["reg_lambda"],
                          num_leaves=params["num_leaves"],
                          #device= "gpu",
                          verbosity=-1,
                          objective=LGBWCEMulti(r=params['r'])
                          )

            clf.fit(
                X_tr, y_tr,
                eval_set=[(X_val, y_val)],
                eval_metric=eval_acc,
                callbacks=[lgb.early_stopping(stopping_rounds=50)],
                )

            y_val_pred = y_val_pred = predict(clf, X_val)
            scores.append(accuracy_score(y_val, y_val_pred))
        return np.mean(scores)


def test(best_params, X, y, X_test, y_test):
    folds = StratifiedKFold(5, random_state=42, shuffle=True)
    scores1 = []
    scores2 = []
    for _, (train_idx, val_idx) in enumerate(folds.split(X, y)):
        X_tr, y_tr = X[train_idx], y[train_idx]
        X_val, y_val = X[val_idx], y[val_idx]

        clf = lgb.LGBMClassifier(
                      n_estimators=1000,
                      num_leaves=best_params['num_leaves'],
                      reg_alpha=best_params['reg_alpha'],
                      reg_lambda=best_params['reg_lambda'],
                      learning_rate=best_params['learning_rate'],
                      #device= "gpu",
                      objective=LGBWCEMulti(r=best_params['r'])
                      )

        clf.fit(
            X_tr,
            y_tr,
            eval_set=[(X_val, y_val)],
            eval_metric=eval_acc,
            callbacks=[lgb.early_stopping(stopping_rounds=50)],
            )

        y_test_pred_prob = predict_proba(clf, X_test)
        y_test_pred = predict(clf, X_test)
        scores1.append(accuracy_score(y_test, y_test_pred))
        scores2.append(f1_score(y_test, y_test_pred, average="weighted"))
    return [scores1, scores2]


def load_data(path):
    with open(path) as f:
        metadata_lines = 0
        for line in f:
            if line.startswith('@'):
                metadata_lines += 1

                if line.startswith('@input'):
                    inputs = [l.strip() for l in line[8:].split(',')]
                elif line.startswith('@output'):
                    outputs = [l.strip() for l in line[8:].split(',')]
            else:
                break

    df = pd.read_csv(path, skiprows=metadata_lines, header=None)
    df.columns = inputs + outputs
    df = pd.concat([pd.get_dummies(df[inputs]), df[outputs]], axis=1)

    matrix = df.values
    X, y = matrix[:, :-1], matrix[:, -1]
    le = LabelEncoder()
    y = le.fit_transform(y)

    return X, y



X, y = load_data('automobile-full.dat')
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=42)


optuna.logging.set_verbosity(optuna.logging.ERROR)
#optuna.logging.set_verbosity(optuna.logging.WARNING)
warnings.filterwarnings("ignore", category=UserWarning)

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(
                direction="maximize",
                sampler=sampler,
                study_name='model_eval',
                )

study.optimize(LGBMulti(X_train, y_train), n_trials=100)
best_params = study.best_trial.params
scores = test(best_params, X_train, y_train, X_test, y_test)

print(scores)
print(f"ACC Mean: {np.mean(scores[1])}\n")
print(f"ACC Std: {np.std(scores[1])}\n")

#print(f"F1 Mean: {np.mean(scores[5])}\n")
#print(f"F1 Std: {np.std(scores[5])}\n")

print(f"F1 Mean: {np.mean(scores[1])}\n")
print(f"F1 Std: {np.std(scores[1])}\n")




Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[8]	valid_0's multi_logloss: -0.0155888	valid_0's eacc: 0.75
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[5]	valid_0's multi_logloss: -1.33473	valid_0's eacc: 0.708333
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[4]	valid_0's multi_logloss: 0.0130967	valid_0's eacc: 0.833333
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[20]	valid_0's multi_logloss: 1.51277	valid_0's eacc: 0.666667
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[3]	valid_0's multi_logloss: -1.06189	valid_0's eacc: 0.782609
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[10]	valid_0's multi_logloss: 0.2193	valid_0's eacc: 0.791667
Training until validation scores don't improve f

单分类lgb

这段代码定义了几个用于二分类问题中损失函数的Python类，每个类实现了一种特定的损失函数计算方式，并能够提供损失函数的梯度(grad)和Hessian矩阵(hess)的值，这对于优化算法尤为重要。下面分别解释每个类的功能和实现细节：

### ACELoss
- **功能**: 实现ACE（Absolute Error Criterion）损失函数。
- **主要参数**:
  - `m`: 一个阈值参数。
  - `clip_value`: 用于概率裁剪，以增加数值稳定性。
- **实现细节**:
  - 使用逻辑斯蒂克函数将预测值转换为概率。
  - 计算调整后的概率`prob_m`。
  - 根据样本的真实标签（`y_true`），分别计算正例和负例的梯度和Hessian。

### ASLLoss
- **功能**: 实现带有类别平衡的Sigmoid损失函数。
- **主要参数**:
  - `r1`, `r2`: 正例和负例的调节参数，用于调整损失函数的平衡。
  - `m`: 阈值参数。
  - `clip_value`: 裁剪概率值，增加数值稳定性。
- **实现细节**:
  - 计算逻辑斯蒂克概率，并裁剪。
  - 使用`grad`和`hess1`、`hess2`方法分别计算正负例的一阶和二阶导数，其中`hess1`和`hess2`分别对应损失函数中不同部分的二阶导数。

### AWELoss
- **功能**: 实现加权交叉熵损失函数。
- **主要参数**:
  - `r1`: 权重参数，调整正例的损失比例。
  - `m`: 阈值参数。
  - `clip_value`: 裁剪概率值，增加数值稳定性。
- **实现细节**:
  - 计算逻辑斯蒂克概率，并裁剪。
  - 使用`grad`和`hess`方法分别计算正负例的一阶和二阶导数。

### FLLoss
- **功能**: 实现Focal Loss，针对难分类的样本给予更大的权重。
- **主要参数**:
  - `r1`: 调整损失函数聚焦能力的参数。
  - `clip_value`: 裁剪概率值，增加数值稳定性。
- **实现细节**:
  - 与`ASLLoss`类似，但对所有样本应用Focal Loss的思路，通过`grad`和`hess1`、`hess2`方法计算损失函数的一阶和二阶导数。

### WCELoss
- **功能**: 实现加权的交叉熵损失函数。
- **主要参数**:
  - `r1`: 权重参数，用于调整正例的损失比例。
  - `clip_value`: 裁剪概率值，增加数值稳定性。
- **实现细节**:
  - 计算逻辑斯蒂克概率，并裁剪。
  - 使用`grad`和`hess`方法分别计算正负例的一阶和二阶导数。

### CBELoss
- **功能**: 实现平衡的交叉熵损失函数。
- **主要参数**:
  - `b`: 平衡参数，用于调整正负样本的平衡。
  - `clip_value`: 裁剪概率值，增加数值稳定性。
- **实现细节**:
  - 计算逻辑斯蒂克概率，并裁剪。
  - 根据正负样本的数量调整损失函数，使得在处理不平衡数据时更加有效。使用`grad`和`hess`方法分别计算正负例的一阶和二阶导数。

### 总结
这些损失函数类通过重载`__call__`方法，为不同的二分类问题提供了定制化的损失计算方法，每个方法都包括了梯度和Hessian矩阵的计算，以便在优化过程中调整模型参数。这些损失函数特别考虑了类别不平衡问题、数值稳定性以及针对难分类样本的聚焦能力等问题。

In [ ]:
import numpy as np


class ACELoss:
    def __init__(self, m, clip_value=1e-7):
        self.m = m
        self.clip_value = clip_value

    def __call__(self, y_true, preds):
        pred = 1 / (1 + np.exp(-preds))
        prob = np.clip(pred, self.clip_value, 1 - self.clip_value)
        prob_m = 1 - np.maximum(prob - self.m, self.clip_value)
        grad = y_true * self.grad(prob) - (1 - y_true) * self.grad(prob_m)
        hess = y_true * self.hess(prob) + (1 - y_true) * self.hess(prob_m)
        return grad, hess

    def grad(self, p):
        return p - 1

    def hess(self, p):
        return p * (1 - p)


class ASLLoss:
    def __init__(self, r1, r2, m, clip_value=1e-7):
        self.r1 = r1
        self.r2 = r2
        self.m = m
        self.clip_value = clip_value

    def __call__(self, y_true, preds):
        pred = 1 / (1 + np.exp(-preds))
        prob = np.clip(pred, self.clip_value, 1 - self.clip_value)
        prob_m = 1 - np.maximum(prob - self.m, self.clip_value)
        grad = y_true * self.grad(prob, self.r1) - (1 - y_true) * self.grad(prob_m, self.r2)
        hess = y_true * (self.hess1(prob, self.r1) + self.hess2(prob, self.r1)) + \
            (1 - y_true) * (self.hess1(prob_m, self.r2) + self.hess2(prob_m, self.r2))
        return grad, hess

    def grad(self, p, r):
        return ((1 - p) ** r) * (r * p * np.log(p) + p - 1)

    def hess1(self, p, r):  # dldp2*dp**2
        return ((1 - p) ** r) * (-r * (r - 1) * p ** 2 * np.log(p) - 2 * r * p * (p - 1) + (p - 1) ** 2)

    def hess2(self, p, r):  # dldp*dp2
        return ((1 - p) ** r) * (1 - 2 * p) * (r * p * np.log(p) + p - 1)



class AWELoss():
    def __init__(self, r1, m, clip_value=1e-7):
        self.r1 = r1
        self.m = m
        self.clip_value = clip_value

    def __call__(self, y_true, preds):
        pred = 1 / (1 + np.exp(-preds))
        prob = np.clip(pred, self.clip_value, 1 - self.clip_value)
        prob_m = 1-np.maximum(prob-self.m, self.clip_value)
        grad = self.r1*y_true*self.grad(prob)-(1-y_true)*self.grad(prob_m)
        hess = self.r1*y_true*self.hess(prob)+(1-y_true)*self.hess(prob_m)
        return grad, hess

    def grad(self, p):
        return p-1

    def hess(self, p):
        return p*(1-p)


class FLLoss:
    def __init__(self, r1, clip_value=1e-7):
        self.r1 = r1
        self.clip_value = clip_value

    def __call__(self, y_true, preds):
        pred = 1 / (1 + np.exp(-preds))
        prob = np.clip(pred, self.clip_value, 1 - self.clip_value)
        grad = y_true * self.grad(prob, self.r1) - (1 - y_true) * self.grad(1 - prob, self.r1)
        hess = y_true * (self.hess1(prob, self.r1) + self.hess2(prob, self.r1)) + \
            (1 - y_true) * (self.hess1(1 - prob, self.r1) + self.hess2(1 - prob, self.r1))
        return grad, hess

    def grad(self, p, r):
        return ((1 - p) ** r) * (r * p * np.log(p) + p - 1)

    def hess1(self, p, r):  # dldp2*dp**2
        return ((1 - p) ** r) * (-r * (r - 1) * p ** 2 * np.log(p) - 2 * r * p * (p - 1) + (p - 1) ** 2)

    def hess2(self, p, r):  # dldp*dp2
        return ((1 - p) ** r) * (1 - 2 * p) * (r * p * np.log(p) + p - 1)


class WCELoss():
    def __init__(self, r1, clip_value=1e-7):
        self.r1 = r1
        self.clip_value = clip_value

    def __call__(self, y_true, preds):
        pred = 1 / (1 + np.exp(-preds))
        prob = np.clip(pred, self.clip_value, 1 - self.clip_value)
        grad = self.r1*y_true*self.grad(prob)-(1-y_true)*self.grad(1-prob)
        hess = self.r1*y_true*(self.hess(prob))+(1-y_true)*(self.hess(1-prob))
        return grad, hess

    def grad(self, p):
        return p-1

    def hess(self, p):
        return p*(1-p)


class CBELoss():
    def __init__(self, b, clip_value=1e-7):
        self.b = b
        self.clip_value = clip_value

    def __call__(self, y_true, preds):
        pred = 1 / (1 + np.exp(-preds))
        prob = np.clip(pred, self.clip_value, 1 - self.clip_value)
        n_pos = np.sum(y_true)
        n_neg = len(y_true)-n_pos
        grad = (1-self.b)/(1-self.b**n_pos)*y_true*self.grad(prob)-(1-self.b)/(1-self.b**n_neg)*(1-y_true)*self.grad(1-prob)
        hess = (1-self.b)/(1-self.b**n_pos)*y_true*(self.hess(prob))+(1-self.b)/(1-self.b**n_neg)*(1-y_true)*(self.hess(1-prob))
        return grad, hess

    def grad(self, p):
        return p-1

    def hess(self, p):
        return p*(1-p)



In [ ]:
import numpy as np
import lightgbm as lgb
from sklearn.metrics import roc_auc_score, f1_score
from sklearn.model_selection import StratifiedKFold
import optuna
from imblearn.datasets import fetch_datasets
from sklearn.model_selection import train_test_split
#from gbdtCBL.binary import ACELoss



def sigmoid(x):
    kEps = 1e-16 #  avoid 0 div
    x = np.minimum(-x, 88.7)  # avoid exp overflow
    return 1 / (1 + np.exp(x)+kEps)


def predict_proba(model, X):
    # Lightgbm: Cannot compute class probabilities or labels due to the usage of customized objective function.
    prediction = model.predict(X)

    prediction_probabilities = sigmoid(prediction).reshape(-1, 1)
    prediction_probabilities = np.concatenate((1 - prediction_probabilities, prediction_probabilities), 1)
    return prediction_probabilities

def eval_auc(labels, preds):  # auc
    p = sigmoid(preds)
    return 'auc', roc_auc_score(labels, p), True


class LGBBinary(object):
    def __init__(self, X, y):

        self.X = X
        self.y = y

    def __call__(self, trial):
        params = {
          "num_leaves": trial.suggest_int("num_leaves", 8, 32),
          "learning_rate": trial.suggest_float("learning_rate", 0.01, 1.0),
          "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 2.0),
          "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 2.0),
          "m": trial.suggest_float("m", 0.05, 0.2),
        }

        folds = StratifiedKFold(5, random_state=42, shuffle=True)
        scores = []
        for _, (train_idx, val_idx) in enumerate(folds.split(self.X, self.y)):
            X_tr, y_tr = self.X[train_idx], self.y[train_idx]
            X_val, y_val = self.X[val_idx], self.y[val_idx]

            clf = lgb.LGBMClassifier(
                          n_estimators=1000,
                          learning_rate=params["learning_rate"],
                          reg_alpha=params["reg_alpha"],
                          reg_lambda=params["reg_lambda"],
                          num_leaves=params["num_leaves"],
                          verbosity=-1,
                          ##device= "gpu",
                          objective=ACELoss(m=params['m']),
                          )

            clf.fit(
                X_tr, y_tr,
                eval_set=[(X_val, y_val)],
                eval_metric=eval_auc,
                callbacks=[lgb.early_stopping(stopping_rounds=50)],
                )

            y_val_pred_prob = predict_proba(clf, X_val)[:, 1]
            scores.append(roc_auc_score(y_val, y_val_pred_prob))
        return np.mean(scores)


def test(best_params, X, y, X_test, y_test):
    folds = StratifiedKFold(5, random_state=42, shuffle=True)
    scores1 = []
    scores2 = []
    for _, (train_idx, val_idx) in enumerate(folds.split(X, y)):
        X_tr, y_tr = X[train_idx], y[train_idx]
        X_val, y_val = X[val_idx], y[val_idx]

        clf = lgb.LGBMClassifier(
                      n_estimators=1000,
                      learning_rate=best_params["learning_rate"],
                      reg_alpha=best_params["reg_alpha"],
                      reg_lambda=best_params["reg_lambda"],
                      num_leaves=best_params["num_leaves"],
                      verbosity=-1,
                      ##device= "gpu",
                      objective=ACELoss(m=best_params['m']),
                      )

        clf.fit(
            X_tr,
            y_tr,
            eval_set=[(X_val, y_val)],
            eval_metric=eval_auc,
            callbacks=[lgb.early_stopping(stopping_rounds=50)],
            )

        y_test_pred_prob = predict_proba(clf, X_test)[:, 1]
        y_test_pred = (y_test_pred_prob >=0.5)+0
        scores1.append(roc_auc_score(y_test, y_test_pred_prob))
        scores2.append(f1_score(y_test, y_test_pred))
    return [scores1, scores2]



data = fetch_datasets()['ecoli']
X, y = data.data, data.target
y = 0.5*y+0.5
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=42)

optuna.logging.set_verbosity(optuna.logging.WARNING)

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(
                direction="maximize",
                sampler=sampler,
                study_name='model_eval',
                )

study.optimize(LGBBinary(X_train, y_train), n_trials=100)
best_params = study.best_trial.params
scores = test(best_params, X_train, y_train, X_test, y_test)


print(f"AUC Mean: {np.mean(scores[0])}\n")
print(f"AUC Std: {np.std(scores[0])}\n")

print(f"F1 Mean: {np.mean(scores[1])}\n")
print(f"F1 Std: {np.std(scores[1])}\n")



# data_list = [
#             'ecoli',
#             'satimage',
#             'sick_euthyroid',
#             'spectrometer',
#             'car_eval_34',
#             'isolet',
#             'us_crime',
#             'libras_move',
#             'thyroid_sick',
#             'arrhythmia',
#             'oil',
#             'yeast_me2',
#             'webpage',
#             'mammography',
#             'protein_homo',
#         ]

Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[5]	valid_0's binary_logloss: 1.70189	valid_0's auc: 0.884783
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[2]	valid_0's binary_logloss: 1.19204	valid_0's auc: 0.855556
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[1]	valid_0's binary_logloss: -0.496612	valid_0's auc: 0.966667
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[3]	valid_0's binary_logloss: 1.05293	valid_0's auc: 0.931111
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[3]	valid_0's binary_logloss: -0.228721	valid_0's auc: 0.964444
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[31]	valid_0's binary_logloss: 2.00152	valid_0's auc: 0.863043
Training until validation scores don't improve 

下面代码实现了一个使用Optuna进行超参数优化，并使用LightGBM处理二分类问题的流程。以下是对代码主要组成部分的详细解释：

### 1. 导入必要的库
- 包含了数据处理(`numpy`, `pandas`), 模型构建(`lightgbm`), 评估指标(`roc_auc_score`, `f1_score`), 数据分割(`StratifiedKFold`, `train_test_split`)，以及超参数优化(`optuna`).

### 2. 定义辅助函数
- **`sigmoid`**: 计算sigmoid函数，用于将模型输出转化为概率。
  
- **`predict_proba`**: 由于使用了自定义的目标函数，需要手动计算类概率。该函数将LightGBM模型的输出通过sigmoid函数转化为概率，并构造出一个二列的概率矩阵，分别代表负类和正类的概率。

- **`eval_auc`**: 自定义评估函数，计算ROC AUC分数，用于在Optuna优化过程中评估模型性能。

### 3. 定义LGBBinary类
这个类用于LightGBM二分类模型的初始化和超参数调优。
- 在`__call__`方法中，使用`StratifiedKFold`进行5折交叉验证。
- 通过Optuna的`trial`对象建议不同的超参数值（如`num_leaves`, `learning_rate`等）。
- 使用建议的超参数训练LightGBM模型，并在验证集上通过`eval_auc`计算ROC AUC分数。

### 4. 测试模型
- **`test` 函数**: 使用最优的超参数组合，在5折交叉验证的每一折上训练模型，并在独立的测试集上评估模型性能，包括ROC AUC和F1分数。

### 5. 数据准备
- 使用`imblearn.datasets.fetch_datasets`加载样本数据集（此处以ecoli为例），并对目标变量`y`进行预处理。
- 通过`train_test_split`将数据分割为训练集和测试集，保持分层的比例。

### 6. Optuna优化过程
- 设置日志等级，创建TPESampler（树结构采样器），并用其初始化一个Optuna研究对象。
- 使用`LGBBinary`类对模型进行优化搜索，寻找最佳超参数组合。

### 7. 输出结果
- 打印测试集上的ROC AUC和F1分数的均值和标准差，以评估模型的泛化能力和稳定性。

### 总结
这段代码通过使用Optuna库对LightGBM模型进行超参数调优，以处理一个二分类问题。展示了从数据预处理、模型训练、超参数搜索到模型评估的完整流程。这样的实现对于在实际应用中优化机器学习模型非常有用。

In [ ]:
import numpy as np
import lightgbm as lgb
from sklearn.metrics import roc_auc_score, f1_score
from sklearn.model_selection import StratifiedKFold
import optuna
from imblearn.datasets import fetch_datasets
from sklearn.model_selection import train_test_split
#from gbdtCBL.binary import ACELoss



def sigmoid(x):
    kEps = 1e-16 #  avoid 0 div
    x = np.minimum(-x, 88.7)  # avoid exp overflow
    return 1 / (1 + np.exp(x)+kEps)


def predict_proba(model, X):
    # Lightgbm: Cannot compute class probabilities or labels due to the usage of customized objective function.
    prediction = model.predict(X)

    prediction_probabilities = sigmoid(prediction).reshape(-1, 1)
    prediction_probabilities = np.concatenate((1 - prediction_probabilities, prediction_probabilities), 1)
    return prediction_probabilities

def eval_auc(labels, preds):  # auc
    p = sigmoid(preds)
    return 'auc', roc_auc_score(labels, p), True


class LGBBinary(object):
    def __init__(self, X, y):

        self.X = X
        self.y = y

    def __call__(self, trial):
        params = {
          "num_leaves": trial.suggest_int("num_leaves", 8, 32),
          "learning_rate": trial.suggest_float("learning_rate", 0.01, 1.0),
          "reg_alpha": trial.suggest_float("reg_alpha", 1e-4, 2.0),
          "reg_lambda": trial.suggest_float("reg_lambda", 1e-4, 2.0),
          "m": trial.suggest_float("m", 0.05, 0.2),
        }

        folds = StratifiedKFold(5, random_state=42, shuffle=True)
        scores = []
        for _, (train_idx, val_idx) in enumerate(folds.split(self.X, self.y)):
            X_tr, y_tr = self.X[train_idx], self.y[train_idx]
            X_val, y_val = self.X[val_idx], self.y[val_idx]

            clf = lgb.LGBMClassifier(
                          n_estimators=1000,
                          learning_rate=params["learning_rate"],
                          reg_alpha=params["reg_alpha"],
                          reg_lambda=params["reg_lambda"],
                          num_leaves=params["num_leaves"],
                          verbosity=-1,
                          ##device= "gpu",
                          objective="binary",
                          )

            clf.fit(
                X_tr, y_tr,
                eval_set=[(X_val, y_val)],
                eval_metric=eval_auc,
                callbacks=[lgb.early_stopping(stopping_rounds=50)],
                )

            y_val_pred_prob = predict_proba(clf, X_val)[:, 1]
            scores.append(roc_auc_score(y_val, y_val_pred_prob))
        return np.mean(scores)


def test(best_params, X, y, X_test, y_test):
    folds = StratifiedKFold(5, random_state=42, shuffle=True)
    scores1 = []
    scores2 = []
    for _, (train_idx, val_idx) in enumerate(folds.split(X, y)):
        X_tr, y_tr = X[train_idx], y[train_idx]
        X_val, y_val = X[val_idx], y[val_idx]

        clf = lgb.LGBMClassifier(
                      n_estimators=1000,
                      learning_rate=best_params["learning_rate"],
                      reg_alpha=best_params["reg_alpha"],
                      reg_lambda=best_params["reg_lambda"],
                      num_leaves=best_params["num_leaves"],
                      verbosity=-1,
                      ##device= "gpu",
                      objective="binary",
                      )

        clf.fit(
            X_tr,
            y_tr,
            eval_set=[(X_val, y_val)],
            eval_metric=eval_auc,
            callbacks=[lgb.early_stopping(stopping_rounds=50)],
            )

        y_test_pred_prob = predict_proba(clf, X_test)[:, 1]
        y_test_pred = (y_test_pred_prob >=0.5)+0
        scores1.append(roc_auc_score(y_test, y_test_pred_prob))
        scores2.append(f1_score(y_test, y_test_pred))
    return [scores1, scores2]



data = fetch_datasets()['ecoli']
X, y = data.data, data.target
y = 0.5*y+0.5
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=42)

optuna.logging.set_verbosity(optuna.logging.WARNING)

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(
                direction="maximize",
                sampler=sampler,
                study_name='model_eval',
                )

study.optimize(LGBBinary(X_train, y_train), n_trials=100)
best_params = study.best_trial.params
scores = test(best_params, X_train, y_train, X_test, y_test)


print(f"AUC Mean: {np.mean(scores[0])}\n")
print(f"AUC Std: {np.std(scores[0])}\n")

print(f"F1 Mean: {np.mean(scores[1])}\n")
print(f"F1 Std: {np.std(scores[1])}\n")



# data_list = [
#             'ecoli',
#             'satimage',
#             'sick_euthyroid',
#             'spectrometer',
#             'car_eval_34',
#             'isolet',
#             'us_crime',
#             'libras_move',
#             'thyroid_sick',
#             'arrhythmia',
#             'oil',
#             'yeast_me2',
#             'webpage',
#             'mammography',
#             'protein_homo',
#         ]

Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[8]	valid_0's binary_logloss: 0.228587	valid_0's auc: 0.897826
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[4]	valid_0's binary_logloss: 0.236397	valid_0's auc: 0.914815
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[9]	valid_0's binary_logloss: 0.113894	valid_0's auc: 0.988889
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[3]	valid_0's binary_logloss: 0.241741	valid_0's auc: 0.868889
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[3]	valid_0's binary_logloss: 0.156917	valid_0's auc: 0.997778
Training until validation scores don't improve for 50 rounds
Early stopping, best iteration is:
[90]	valid_0's binary_logloss: 0.253416	valid_0's auc: 0.884783
Training until validation scores don't improv

多分类xgb

In [ ]:
import numpy as np
from sklearn.preprocessing import OneHotEncoder


def softmax(x):
    kEps = 1e-16  # avoid 0 div
    x = np.minimum(x, 88.7)  # avoid exp overflow
    e = np.exp(x)
    return e / np.expand_dims(np.sum(e, axis=1)+kEps, axis=1)


class XGBACEMulti():
    def __init__(self, m):
        self.m = m

    def __call__(self, labels, preds):
        p = softmax(preds)
        pm = np.maximum(p-self.m, 1e-7)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        grad = -encoded_label*(encoded_label-p)-(1-encoded_label)*(encoded_label-pm)
        hess = encoded_label*(encoded_label-p)*(encoded_label+p-1)+(1-encoded_label)*(encoded_label-pm)*(encoded_label+pm-1)
        return grad.reshape(grad.shape[0]*grad.shape[1]), hess.reshape(hess.shape[0]*hess.shape[1])



class XGBASLMulti():
    def __init__(self, r1, r2, m):
        self.r1 = r1
        self.r2 = r2
        self.m = m

    def __call__(self, labels, preds):
        p = softmax(preds)
        pm = np.maximum(p-self.m, 1e-7)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        pt = np.sum(p*encoded_label, axis=1, keepdims=True)

        grad = encoded_label*self.dldpXp(pt, self.r1)*(encoded_label-p)+\
              (1-encoded_label)*self.dldpXp(pt, self.r2)*(encoded_label-pm)
        hess = encoded_label*(self.dldp2Xp2(pt, self.r1)*(encoded_label-p)**2+\
              self.dldpXp(pt, self.r1)*(encoded_label-p)*(1-2*p))+\
               (1-encoded_label)*(self.dldp2Xp2(pt, self.r2)*(encoded_label-pm)**2+\
              self.dldpXp(pt, self.r2)*(encoded_label-pm)*(1-2*pm))

        return grad.reshape(grad.shape[0]*grad.shape[1]), hess.reshape(hess.shape[0]*hess.shape[1])

    def dldpXp(self, p, r):  # dldp*p
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = (1-p1)**(r-1)*(r*p1*np.log(p1)+p1-1)
        return result

    def dldp2Xp2(self, p, r):  # dldp2*p**2
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = -(1-p1)**(r-2)*(r*(r-1)*p1**2*np.log(p1)+2*r*p1*(p1-1)-(p1-1)**2)
        return result



class XGBAWEMulti():
    def __init__(self, r, m):
        self.r = r
        self.m = m

    def __call__(self, labels, preds):
        p = softmax(preds)
        pm = np.maximum(p-self.m, 1e-7)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        grad = -self.r*encoded_label*(encoded_label-p)-(1-encoded_label)*(encoded_label-pm)
        hess = self.r*encoded_label*(encoded_label-p)*(encoded_label+p-1)+(1-encoded_label)*(encoded_label-pm)*(encoded_label+pm-1)
        return grad.reshape(grad.shape[0]*grad.shape[1]), hess.reshape(hess.shape[0]*hess.shape[1])



class XGBFLMulti():
    def __init__(self, r):
        self.r = r

    def __call__(self, labels, preds):
        p = softmax(preds)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        pt = np.sum(p*encoded_label, axis=1, keepdims=True)

        grad = self.dldpXp(pt)*(encoded_label-p)
        hess = self.dldp2Xp2(pt)*(encoded_label-p)**2+\
            self.dldpXp(pt)*(encoded_label-p)*(1-2*p)

        return grad.reshape(grad.shape[0]*grad.shape[1]), hess.reshape(hess.shape[0]*hess.shape[1])

    def dldpXp(self, p):  # dldp*p
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = (1-p1)**(self.r-1)*(self.r*p1*np.log(p1)+p1-1)
        return result

    def dldp2Xp2(self, p):  # dldp2*p**2
        result = np.zeros(p.shape)
        p1 = p[(0<p)&(p<1)]
        result[(0<p)&(p<1)] = -(1-p1)**(self.r-2)*(self.r*(self.r-1)*p1**2*np.log(p1)+\
            2*self.r*p1*(p1-1)-(p1-1)**2)
        return result



class XGBWCEMulti():
    def __init__(self, r):
        self.r = r

    def __call__(self, labels, preds):
        p = softmax(preds)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        grad = -self.r*encoded_label*(encoded_label-p)-(1-encoded_label)*(encoded_label-p)
        hess = self.r*encoded_label*(encoded_label-p)*(encoded_label+p-1)+(1-encoded_label)*(encoded_label-p)*(encoded_label+p-1)
        return grad.reshape(grad.shape[0]*grad.shape[1]), hess.reshape(hess.shape[0]*hess.shape[1])


class XGBCBEMulti():
    def __init__(self, b):
        self.b = b

    def __call__(self, labels, preds):
        p = softmax(preds)
        grad = np.zeros(preds.shape)
        hess = np.zeros(preds.shape)
        encoder = OneHotEncoder()
        encoded_label = encoder.fit_transform(labels.reshape(-1, 1)).toarray()

        n_pos = np.sum(labels, axis=0)
        ratio = (1-self.b)/(1-self.b**n_pos)
        grad = p-encoded_label
        hess = (encoded_label-p)*(encoded_label+p-1)

        grad *= ratio
        hess *= ratio
        return grad.reshape(grad.shape[0]*grad.shape[1]), hess.reshape(hess.shape[0]*hess.shape[1])


In [ ]:
import numpy as np
import xgboost as xgb
from sklearn.metrics import accuracy_score, f1_score
from sklearn.model_selection import StratifiedKFold
import optuna
from sklearn.model_selection import train_test_split
import pandas as pd
from sklearn.preprocessing import LabelEncoder
#from gbdtCBL.xgbmulti import XGBFLMulti



class XGBMulti(object):
    def __init__(self, X, y):

        self.X = X
        self.y = y

    def __call__(self, trial):
        params = {
        'max_depth': trial.suggest_int('max_depth', 2, 10),
        'reg_alpha': trial.suggest_float('reg_alpha', 1e-4, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 1e-4, 5.0),
        'learning_rate': trial.suggest_float('learning_rate', 1e-3, 1.0),
        "r": trial.suggest_categorical("r", [0.5, 1.0, 2.0]),
        }

        folds = StratifiedKFold(5, random_state=42, shuffle=True)
        scores = []
        for _, (train_idx, val_idx) in enumerate(folds.split(self.X, self.y)):
            X_tr, y_tr = self.X[train_idx], self.y[train_idx]
            X_val, y_val = self.X[val_idx], self.y[val_idx]

            clf = xgb.XGBClassifier(
                                    n_estimators=1000,
                                    learning_rate=params["learning_rate"],
                                    reg_alpha=params["reg_alpha"],
                                    reg_lambda=params["reg_lambda"],
                                    max_depth=params["max_depth"],
                                    #device= "cuda",
                                    verbosity=2,
                                    tree_method="hist",
                                    early_stopping_rounds=50,
                                    objective=XGBFLMulti(r=params['r'])
                                    )

            clf.fit(
                    X_tr, y_tr,
                    eval_set=[(X_val, y_val)],
                    )

            y_val_pred_prob = clf.predict_proba(X_val)
            y_val_pred = clf.predict(X_val)
            scores.append(accuracy_score(y_val, y_val_pred))
        return np.mean(scores)


def test(best_params, X, y, X_test, y_test):
    folds = StratifiedKFold(5, random_state=42, shuffle=True)
    scores1 = []
    scores2 = []
    for _, (train_idx, val_idx) in enumerate(folds.split(X, y)):
        X_tr, y_tr = X[train_idx], y[train_idx]
        X_val, y_val = X[val_idx], y[val_idx]

        clf = xgb.XGBClassifier(
                                n_estimators=1000,
                                learning_rate=best_params["learning_rate"],
                                reg_alpha=best_params["reg_alpha"],
                                reg_lambda=best_params["reg_lambda"],
                                max_depth=best_params["max_depth"],
                                #device= "cuda",
                                verbosity=2,
                                tree_method="hist",
                                early_stopping_rounds=50,
                                objective=XGBFLMulti(r=best_params['r'])
                                )

        clf.fit(
                X_tr,
                y_tr,
                eval_set=[(X_val, y_val)],
                )

        y_test_pred_prob = clf.predict_proba(X_test)
        y_test_pred = clf.predict(X_test)
        scores1.append(accuracy_score(y_test, y_test_pred))
        scores2.append(f1_score(y_test, y_test_pred, average="weighted"))
    return [scores1, scores2]


def load_data(path):
    with open(path) as f:
        metadata_lines = 0
        for line in f:
            if line.startswith('@'):
                metadata_lines += 1

                if line.startswith('@input'):
                    inputs = [l.strip() for l in line[8:].split(',')]
                elif line.startswith('@output'):
                    outputs = [l.strip() for l in line[8:].split(',')]
            else:
                break

    df = pd.read_csv(path, skiprows=metadata_lines, header=None)
    df.columns = inputs + outputs
    df = pd.concat([pd.get_dummies(df[inputs]), df[outputs]], axis=1)

    matrix = df.values
    X, y = matrix[:, :-1], matrix[:, -1]
    le = LabelEncoder()
    y = le.fit_transform(y)

    return X, y



X, y = load_data('automobile-full.dat')
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=42)

optuna.logging.set_verbosity(optuna.logging.WARNING)

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(
                            direction="maximize",
                            sampler=sampler,
                            study_name='model_eval',
                            )

study.optimize(XGBMulti(X_train, y_train), n_trials=10)
#study.optimize(XGBMulti(X_train, y_train), n_trials=100)
best_params = study.best_trial.params
scores = test(best_params, X_train, y_train, X_test, y_test)


print(f"ACC Mean: {np.mean(scores[0])}\n")
print(f"ACC Std: {np.std(scores[0])}\n")

print(f"F1 Mean: {np.mean(scores[1])}\n")
print(f"F1 Std: {np.std(scores[1])}\n")



[0]	validation_0-mlogloss:1.19663
[1]	validation_0-mlogloss:0.99071
[2]	validation_0-mlogloss:0.89678
[3]	validation_0-mlogloss:0.82810
[4]	validation_0-mlogloss:0.78905
[5]	validation_0-mlogloss:0.76211
[6]	validation_0-mlogloss:0.74419
[7]	validation_0-mlogloss:0.72923
[8]	validation_0-mlogloss:0.71423
[9]	validation_0-mlogloss:0.70160
[10]	validation_0-mlogloss:0.69956
[11]	validation_0-mlogloss:0.69810
[12]	validation_0-mlogloss:0.69830
[13]	validation_0-mlogloss:0.69514
[14]	validation_0-mlogloss:0.68914
[15]	validation_0-mlogloss:0.69136
[16]	validation_0-mlogloss:0.69113
[17]	validation_0-mlogloss:0.69010
[18]	validation_0-mlogloss:0.69096
[19]	validation_0-mlogloss:0.68972
[20]	validation_0-mlogloss:0.68962
[21]	validation_0-mlogloss:0.69009
[22]	validation_0-mlogloss:0.68725
[23]	validation_0-mlogloss:0.68722


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n

[24]	validation_0-mlogloss:0.68653
[25]	validation_0-mlogloss:0.68593
[26]	validation_0-mlogloss:0.68593
[27]	validation_0-mlogloss:0.68593
[28]	validation_0-mlogloss:0.68593
[29]	validation_0-mlogloss:0.68594
[30]	validation_0-mlogloss:0.68594
[31]	validation_0-mlogloss:0.68595
[32]	validation_0-mlogloss:0.68551
[33]	validation_0-mlogloss:0.68551
[34]	validation_0-mlogloss:0.68551
[35]	validation_0-mlogloss:0.68551
[36]	validation_0-mlogloss:0.68552
[37]	validation_0-mlogloss:0.68552
[38]	validation_0-mlogloss:0.68552
[39]	validation_0-mlogloss:0.68553
[40]	validation_0-mlogloss:0.68553
[41]	validation_0-mlogloss:0.68553
[42]	validation_0-mlogloss:0.68553
[43]	validation_0-mlogloss:0.68553
[44]	validation_0-mlogloss:0.68553
[45]	validation_0-mlogloss:0.68553
[46]	validation_0-mlogloss:0.68553
[47]	validation_0-mlogloss:0.68553
[48]	validation_0-mlogloss:0.68553
[49]	validation_0-mlogloss:0.68553


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n

[50]	validation_0-mlogloss:0.68553
[51]	validation_0-mlogloss:0.68553
[52]	validation_0-mlogloss:0.68553
[53]	validation_0-mlogloss:0.68553
[54]	validation_0-mlogloss:0.68553
[55]	validation_0-mlogloss:0.68553
[56]	validation_0-mlogloss:0.68553
[57]	validation_0-mlogloss:0.68553
[58]	validation_0-mlogloss:0.68553
[59]	validation_0-mlogloss:0.68553
[60]	validation_0-mlogloss:0.68553
[61]	validation_0-mlogloss:0.68553
[62]	validation_0-mlogloss:0.68553
[63]	validation_0-mlogloss:0.68553
[64]	validation_0-mlogloss:0.68553
[65]	validation_0-mlogloss:0.68553
[66]	validation_0-mlogloss:0.68553
[67]	validation_0-mlogloss:0.68553
[68]	validation_0-mlogloss:0.68553
[69]	validation_0-mlogloss:0.68553
[70]	validation_0-mlogloss:0.68553
[71]	validation_0-mlogloss:0.68553
[72]	validation_0-mlogloss:0.68553
[73]	validation_0-mlogloss:0.68553
[74]	validation_0-mlogloss:0.68553
[75]	validation_0-mlogloss:0.68553
[76]	validation_0-mlogloss:0.68553
[77]	validation_0-mlogloss:0.68553


...

[40]	validation_0-mlogloss:0.66806
[41]	validation_0-mlogloss:0.66806


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(


[42]	validation_0-mlogloss:0.66806
[43]	validation_0-mlogloss:0.66806
[44]	validation_0-mlogloss:0.66806
[45]	validation_0-mlogloss:0.66806
[46]	validation_0-mlogloss:0.66806
[47]	validation_0-mlogloss:0.66806
[48]	validation_0-mlogloss:0.66806
[49]	validation_0-mlogloss:0.66806
[50]	validation_0-mlogloss:0.66806
[51]	validation_0-mlogloss:0.66806
[52]	validation_0-mlogloss:0.66806
[53]	validation_0-mlogloss:0.66806
[54]	validation_0-mlogloss:0.66806
[55]	validation_0-mlogloss:0.66806
[56]	validation_0-mlogloss:0.66806
[57]	validation_0-mlogloss:0.66806
[58]	validation_0-mlogloss:0.66806
[59]	validation_0-mlogloss:0.66806


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n_samples, n_targets) or (n_samples, n_classes).
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:2150: FutureWarning: Since 2.1.0, the shape of the gradient and hessian is required to be (n

ACC Mean: 0.8150000000000001

ACC Std: 0.07516648189186453

F1 Mean: 0.8057396540657411

F1 Std: 0.07909469729086083



单分类xgb

In [ ]:
import numpy as np
import xgboost as xgb
from sklearn.metrics import roc_auc_score, f1_score
from sklearn.model_selection import StratifiedKFold
import optuna
from imblearn.datasets import fetch_datasets
from sklearn.model_selection import train_test_split
#from gbdtCBL.binary import ASLLoss



class XGBBinary(object):
    def __init__(self, X, y):

        self.X = X
        self.y = y

    def __call__(self, trial):
        params = {
            'max_depth': trial.suggest_int('max_depth', 2, 10),
            'reg_alpha': trial.suggest_float('reg_alpha', 1e-4, 1.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 1e-4, 5.0),
            'learning_rate': trial.suggest_float('learning_rate', 1e-3, 1.0),
            "r1": trial.suggest_categorical("r1", [0.0, 0.1]),
            "r2": trial.suggest_categorical("r2", [0.5, 1.0, 2.0]),
            "m": trial.suggest_float("m", 0.05, 0.2),
        }

        folds = StratifiedKFold(5, random_state=42, shuffle=True)
        scores = []
        for _, (train_idx, val_idx) in enumerate(folds.split(self.X, self.y)):
            X_tr, y_tr = self.X[train_idx], self.y[train_idx]
            X_val, y_val = self.X[val_idx], self.y[val_idx]

            clf = xgb.XGBClassifier(
                                    n_estimators=1000,
                                    learning_rate=params["learning_rate"],
                                    reg_alpha=params["reg_alpha"],
                                    reg_lambda=params["reg_lambda"],
                                    max_depth=params["max_depth"],
                                    #device= "cuda",
                                    #verbosity=2,
                                    tree_method="hist",
                                    early_stopping_rounds=50,
                                    objective=ASLLoss(r1=params['r1'],
                                                      r2=params['r2'],
                                                      m=params['m']),
                                    )

            clf.fit(
                    X_tr, y_tr,
                    eval_set=[(X_val, y_val)],
                    )

            y_val_pred_prob = clf.predict_proba(X_val)[:, 1]
            y_val_pred = clf.predict(X_val)
            scores.append(roc_auc_score(y_val, y_val_pred_prob))
        return np.mean(scores)


def test(best_params, X, y, X_test, y_test):
    folds = StratifiedKFold(5, random_state=42, shuffle=True)
    scores1 = []
    scores2 = []
    for _, (train_idx, val_idx) in enumerate(folds.split(X, y)):
        X_tr, y_tr = X[train_idx], y[train_idx]
        X_val, y_val = X[val_idx], y[val_idx]

        clf = xgb.XGBClassifier(
                                n_estimators=1000,
                                learning_rate=best_params["learning_rate"],
                                reg_alpha=best_params["reg_alpha"],
                                reg_lambda=best_params["reg_lambda"],
                                max_depth=best_params["max_depth"],
                                #device= "cuda",
                                #verbosity=2,
                                tree_method="hist",
                                early_stopping_rounds=50,
                                objective=ASLLoss(r1=best_params['r1'],
                                                  r2=best_params['r2'],
                                                  m=best_params['m']),
                                )

        clf.fit(
                X_tr,
                y_tr,
                eval_set=[(X_val, y_val)],
                )

        y_test_pred_prob = clf.predict_proba(X_test)[:, 1]
        y_test_pred = clf.predict(X_test)
        scores1.append(roc_auc_score(y_test, y_test_pred_prob))
        scores2.append(f1_score(y_test, y_test_pred))
    return [scores1, scores2]



data = fetch_datasets()['ecoli']
X, y = data.data, data.target
y = 0.5*y+0.5
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=42)

optuna.logging.set_verbosity(optuna.logging.WARNING)

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(
                            direction="maximize",
                            sampler=sampler,
                            study_name='model_eval',
                            )

study.optimize(XGBBinary(X_train, y_train), n_trials=100)
best_params = study.best_trial.params
scores = test(best_params, X_train, y_train, X_test, y_test)


print(f"AUC Mean: {np.mean(scores[0])}\n")
print(f"AUC Std: {np.std(scores[0])}\n")

print(f"F1 Mean: {np.mean(scores[1])}\n")
print(f"F1 Std: {np.std(scores[1])}\n")



流式输出内容被截断，只能显示最后 5000 行内容。
[68]	validation_0-logloss:0.36131
[69]	validation_0-logloss:0.36131
[0]	validation_0-logloss:0.54615
[1]	validation_0-logloss:0.47069
[2]	validation_0-logloss:0.43459
[3]	validation_0-logloss:0.41534
[4]	validation_0-logloss:0.40624
[5]	validation_0-logloss:0.39276
[6]	validation_0-logloss:0.39841
[7]	validation_0-logloss:0.39433
[8]	validation_0-logloss:0.39031
[9]	validation_0-logloss:0.38964
[10]	validation_0-logloss:0.38728
[11]	validation_0-logloss:0.38798
[12]	validation_0-logloss:0.38555
[13]	validation_0-logloss:0.38606
[14]	validation_0-logloss:0.38464
[15]	validation_0-logloss:0.38778
[16]	validation_0-logloss:0.38673
[17]	validation_0-logloss:0.38690
[18]	validation_0-logloss:0.38541
[19]	validation_0-logloss:0.38624
[20]	validation_0-logloss:0.38533
[21]	validation_0-logloss:0.38598
[22]	validation_0-logloss:0.38461
[23]	validation_0-logloss:0.38558
[24]	validation_0-logloss:0.38256
[25]	validation_0-logloss:0.38169
[26]	validation_0-logloss:0.383